In [1]:
import pandas as pd
import os
from fuc import pyvcf
from tqdm.notebook import tqdm
import pybedtools
import numpy as np
import networkx
import datetime
import warnings

tqdm.pandas()

<h1> Read the data </h1>

In [2]:
basedir = "/home/vfishman/projects/regina_deafness/"

samples = [f for f in os.listdir(basedir) if os.path.isdir(f) and f.find("Gen")!=-1]
samples

['19412RT-Gen005-PCRfree-30X',
 '19412E-Gen001-PCRfree',
 '19412JR-Gen005-PCRfree-30X',
 '20487A-Gen001-PCRfree',
 '20487-Gen001-PCRfree',
 '20487J-Gen001-PCRfree',
 '20487N-Gen001-PCRfree',
 '19412AL-Gen005-PCRfree-30X']

In [3]:
SVs = []

# read all vcf files

sv_caller_files = {"cue":"/reports/svs.vcf",
                  "delly_sv":"/delly/delly.sv.vcf"
                  }

SVs = {}

for sample in tqdm(samples):
    for sv_caller,sv_caller_file in sv_caller_files.items():
        fname = os.path.join(basedir,sample) + sv_caller_file
        vcfFrame = pyvcf.VcfFrame.from_file(fname)
        vcfFrame.name = sample+":"+sv_caller
        SVs[vcfFrame.name] = vcfFrame

# convert to bed_file with name correspoding to SV id

# merge overlapping intervals keeping track of ids

# construct any query

  0%|          | 0/8 [00:00<?, ?it/s]

In [4]:
next(SVs.values().__iter__()).name

'19412RT-Gen005-PCRfree-30X:cue'

In [5]:
def vcfFrame2bed(vf, extend = 0):   
    chrm = vf.df["CHROM"]
    start = (vf.df["POS"] - extend).apply(lambda x: max(x,0))
    try:
        end = (vf.df.apply(pyvcf.row_parseinfo, args=('END',), axis=1).astype(int) + extend)
    except:
        print (vf.name, vf.caller)
        raise
    svtype = vf.df.apply(pyvcf.row_parseinfo, args=('SVTYPE',), axis=1).astype(str) 
    svtype = svtype.apply(lambda x: x.replace("IDUP","DUP"))
    breakpoints_df = pd.DataFrame({"chrm":chrm,
                         "start":start,
                         "end":end,
                         "SV_type":svtype,
                         "FILTER":vf.df["FILTER"].values}
                       )

    # represent inversions as two breakpoints, one for each inversion side
    breakpoints_inv = breakpoints_df.query("SV_type=='INV'")
    n_iversions = len(breakpoints_inv)
    n_total = len(breakpoints_df)
    
    breakpoints_inv_start = pd.DataFrame(breakpoints_inv, copy=True)
    breakpoints_inv_end = pd.DataFrame(breakpoints_inv, copy=True)

    breakpoints_inv_start.loc[:,"end"] = breakpoints_inv_start["start"]+2*extend + 1
    breakpoints_inv_end.loc[:,"start"] = (breakpoints_inv_end["end"]-2*extend-1).apply(lambda x: max(x,0))
    breakpoints_inv = pd.concat([breakpoints_inv_start,breakpoints_inv_end]).reset_index(drop=True)
    
    breakpoints_df = pd.concat([breakpoints_df.query("SV_type!='INV'"),
                                breakpoints_inv]
                              ).reset_index(drop=True)
    # print (len(breakpoints_df) , n_total , n_iversions, len(breakpoints_inv), len(breakpoints_inv_start),len(breakpoints_inv_end))
    assert len(breakpoints_df) == n_total + n_iversions
    name = (pd.Series(breakpoints_df.index.values).astype(str) + ":"+vf.name).values
    breakpoints_df["name"] = name

    return breakpoints_df

In [6]:
SVs_bed = list(map(vcfFrame2bed,tqdm(SVs.values())))

  0%|          | 0/16 [00:00<?, ?it/s]

In [7]:
SVs_bed_combined = pd.concat(SVs_bed)

In [8]:
SVs_bed_combined

chrm      start        end SV_type   FILTER  \
0                     chr14   40140613   40148469     DEL     PASS   
1                     chr14   79639949   79648707     DEL     PASS   
2                     chr14   35136247   35145840     DEL     PASS   
3                     chr14   18539053   18547319     DEL     PASS   
4                     chr14  105906883  105916674     DEL     PASS   
...                     ...        ...        ...     ...      ...   
53167      chrUn_GL000216v2     173813     173814     INV  LowQual   
53168  chr16_KI270853v1_alt     742298     742299     INV  LowQual   
53169  chr16_KI270853v1_alt    2029973    2029974     INV  LowQual   
53170  chr16_KI270853v1_alt    1984888    1984889     INV     PASS   
53171  chr16_KI270853v1_alt    1984889    1984890     INV     PASS   

                                            name  
0               0:19412RT-Gen005-PCRfree-30X:cue  
1               1:19412RT-Gen005-PCRfree-30X:cue  
2               2:19412RT-Gen005-PCRfree-30X:cue  
3               3:19412RT-Gen005-PCRfree-30X:cue  
4               4:19412RT-Gen005-PCRfree-30X:cue  
...                                          ...  
53167  53167:19412AL-Gen005-PCRfree-30X:delly_sv  
53168  53168:19412AL-Gen005-PCRfree-30X:delly_sv  
53169  53169:19412AL-Gen005-PCRfree-30X:delly_sv  
53170  53170:19412AL-Gen005-PCRfree-30X:delly_sv  
53171  53171:19412AL-Gen005-PCRfree-30X:delly_sv  

[606505 rows x 6 columns]

In [9]:
SVs_bed_combined.SV_type.value_counts()

DEL    217283
INV    215032
BND    122396
DUP     45555
INS      6239
Name: SV_type, dtype: int64

In [10]:
SVs_bed_combined["FILTER"].value_counts()

LowQual    456376
PASS       150129
Name: FILTER, dtype: int64

In [11]:
SVs_bed_combined["length"] = SVs_bed_combined["end"] - SVs_bed_combined["start"]

In [12]:
agg = SVs_bed_combined.groupby("SV_type")["length"].agg(["min","max","mean","std"])
assert np.all([i in ['BND', 'DEL', 'DUP', 'INS', 'INV'] for i in agg.index])
BND_types = ["BND","INS","INV"]
assert agg.loc[BND_types,"max"].max()<10
agg

min        max          mean           std
SV_type                                            
BND        1          1  1.000000e+00  0.000000e+00
DEL       16  242323058  1.744821e+06  1.421276e+07
DUP       60  242323169  5.229671e+06  2.293732e+07
INS        1          3  1.003847e+00  6.444535e-02
INV        1          1  1.000000e+00  0.000000e+00

<h1> Aggregate and overlap the data </h1>

In [15]:
def get_merged_intervals_BND(SVs_bed_combined_singe_type, merge_dist = 500):
    btool = pybedtools.BedTool.from_dataframe(
        SVs_bed_combined_singe_type[["chrm","start","end","name","SV_type"]])
    with warnings.catch_warnings():
        warnings.simplefilter("ignore")
        merged = btool.sort().merge(c=4,o="collapse",d=merge_dist).to_dataframe()
    ids = pd.Series(merged.index.values).astype(str).values
    svtype = ":" + SVs_bed_combined_singe_type.name
    merged_intevalIndex = ids + svtype
    merged["interval_index"] = merged_intevalIndex 
    return merged

def get_merged_intervals_CNV(SVs_bed_combined_singe_type, min_merge_overlap = 0.7):
    colnames = ["chrm","start","end","name","SV_type"]
    btool = pybedtools.BedTool.from_dataframe(
            SVs_bed_combined_singe_type[colnames])
    print (datetime.datetime.now(), "Sorting data")
    with warnings.catch_warnings():
        warnings.simplefilter("ignore")
        sorted_bt = btool.sort()

    print (datetime.datetime.now(), "Computing intersection")
    with warnings.catch_warnings():
        warnings.simplefilter("ignore")
        intersect = sorted_bt.intersect(sorted_bt, 
                                     f=min_merge_overlap,
                                     r=True, sorted=True,
                                     wa=True, wb=True)\
                       .to_dataframe()
    print (datetime.datetime.now(), "Converting to graph")

    # note wierd names of columns 'name', 'itemRgb'
    # these are default bedtools names
    g = networkx.from_pandas_edgelist(intersect, source='name', target='itemRgb')
    # networkx.draw(g)
    assert not g.is_directed()
   
    print (datetime.datetime.now(), "Getting clusters")
    clusters = networkx.connected_components(g)
    sorted_as_df = sorted_bt.to_dataframe()
    sorted_as_df.columns = colnames

    print (datetime.datetime.now(), "Setting clusters info")
    sorted_as_df["interval_index"] = pd.NA
    assert not np.any(sorted_as_df["name"].duplicated())
    sorted_as_df = sorted_as_df.set_index("name")
    for cluster_id,cluster in tqdm(enumerate(clusters)):
        sorted_as_df.loc[list(cluster),"interval_index"] = str(cluster_id)
    sorted_as_df.loc[:,"interval_index"] = sorted_as_df.apply(
                                                lambda x: x["interval_index"]+":"+x["SV_type"],
                                                axis="columns"
                                            )
    print (datetime.datetime.now(), "Aggregating clusters")
    return sorted_as_df.reset_index(drop=False).groupby("interval_index").agg({
                                    "name": lambda x: ",".join(x),
                                    "start": min,
                                    "end": max,
                                    "SV_type":lambda x: list(x)[0],
                                    "chrm":lambda x: list(x)[0]
                                    }
                                ).reset_index(drop=False).rename(columns={"chrm":"chrom"})



In [16]:
SVs_bed_combined_merged_intervals_CNV = \
    SVs_bed_combined.query("SV_type in ['DEL','DUP']").\
                     groupby("SV_type").\
                     progress_apply(get_merged_intervals_CNV)

  0%|          | 0/2 [00:00<?, ?it/s]

2023-06-20 10:35:50.647146 Sorting data
2023-06-20 10:35:51.668129 Computing intersection
2023-06-20 10:36:25.912828 Converting to graph
2023-06-20 10:36:41.961513 Getting clusters
2023-06-20 10:36:42.253822 Setting clusters info


0it [00:00, ?it/s]

2023-06-20 10:38:09.848323 Aggregating clusters
2023-06-20 10:38:26.894403 Sorting data
2023-06-20 10:38:27.109105 Computing intersection
2023-06-20 10:38:54.551000 Converting to graph
2023-06-20 10:39:06.338129 Getting clusters
2023-06-20 10:39:06.391662 Setting clusters info


0it [00:00, ?it/s]

2023-06-20 10:39:12.029881 Aggregating clusters


In [17]:
SVs_bed_combined_merged_intervals_CNV.reset_index(drop=True, inplace=True)
SVs_bed_combined_merged_intervals_CNV

interval_index                                               name  \
0               0:DEL  0:19412E-Gen001-PCRfree:delly_sv,0:19412RT-Gen...   
1          100000:DEL               12512:20487A-Gen001-PCRfree:delly_sv   
2          100001:DEL               12513:20487A-Gen001-PCRfree:delly_sv   
3          100002:DEL  12201:20487J-Gen001-PCRfree:delly_sv,14742:204...   
4          100003:DEL               12202:20487J-Gen001-PCRfree:delly_sv   
...               ...                                                ...   
128737        997:DUP  23336:19412E-Gen001-PCRfree:delly_sv,20183:204...   
128738        998:DUP  33564:19412JR-Gen005-PCRfree-30X:delly_sv,2745...   
128739        999:DUP  23738:20487N-Gen001-PCRfree:delly_sv,19815:204...   
128740         99:DUP                  325:20487-Gen001-PCRfree:delly_sv   
128741          9:DUP                  32:20487A-Gen001-PCRfree:delly_sv   

           start       end SV_type  chrom  
0          10511    181112     DEL   chr1  
1       21935833  21937427     DEL   chr7  
2       21937199  21938944     DEL   chr7  
3       21956360  21956407     DEL   chr7  
4       21956499  21957528     DEL   chr7  
...          ...       ...     ...    ...  
128737  55057761  55057929     DUP  chr11  
128738  55232550  55233450     DUP  chr11  
128739  55240268  55241810     DUP  chr11  
128740  43904745  43905872     DUP   chr1  
128741   1670616  21803665     DUP   chr1  

[128742 rows x 6 columns]

In [18]:
SVs_bed_combined_merged_intervals_BND = \
    SVs_bed_combined.query("SV_type in @BND_types").\
                     groupby("SV_type").\
                     progress_apply(get_merged_intervals_BND)

  0%|          | 0/3 [00:00<?, ?it/s]

In [19]:
SVs_bed_combined_merged_intervals_BND = \
    SVs_bed_combined_merged_intervals_BND.reset_index().drop(columns=["level_1"])
SVs_bed_combined_merged_intervals_BND

SV_type              chrom     start       end  \
0          BND       HLA-A*01:11N      1291      1292   
1          BND  HLA-A*02:01:01:01      3068      3069   
2          BND  HLA-A*02:01:01:03       163       164   
3          BND  HLA-A*02:01:01:03      1541      1542   
4          BND  HLA-A*02:01:01:04      2016      2017   
...        ...                ...       ...       ...   
164181     INV               chrY  56866857  56866858   
164182     INV               chrY  56874438  56874439   
164183     INV               chrY  56876114  56876115   
164184     INV               chrY  56879098  56879099   
164185     INV               chrY  56880008  56880492   

                                                     name interval_index  
0                    51658:19412E-Gen001-PCRfree:delly_sv          0:BND  
1               46570:19412AL-Gen005-PCRfree-30X:delly_sv          1:BND  
2               54194:19412RT-Gen005-PCRfree-30X:delly_sv          2:BND  
3                    50708:20487N-Gen001-PCRfree:delly_sv          3:BND  
4                    51659:19412E-Gen001-PCRfree:delly_sv          4:BND  
...                                                   ...            ...  
164181               79445:20487A-Gen001-PCRfree:delly_sv     113128:INV  
164182               77654:20487N-Gen001-PCRfree:delly_sv     113129:INV  
164183              104836:20487N-Gen001-PCRfree:delly_sv     113130:INV  
164184              114386:20487A-Gen001-PCRfree:delly_sv     113131:INV  
164185  79446:20487A-Gen001-PCRfree:delly_sv,114387:20...     113132:INV  

[164186 rows x 6 columns]

In [20]:
assert set(SVs_bed_combined_merged_intervals_BND.columns.values) == \
       set(SVs_bed_combined_merged_intervals_CNV.columns.values)

In [21]:
SVs_bed_combined_merged_intervals = pd.concat([SVs_bed_combined_merged_intervals_BND,SVs_bed_combined_merged_intervals_CNV]).reset_index(drop=True)
SVs_bed_combined_merged_intervals

SV_type              chrom     start       end  \
0          BND       HLA-A*01:11N      1291      1292   
1          BND  HLA-A*02:01:01:01      3068      3069   
2          BND  HLA-A*02:01:01:03       163       164   
3          BND  HLA-A*02:01:01:03      1541      1542   
4          BND  HLA-A*02:01:01:04      2016      2017   
...        ...                ...       ...       ...   
292923     DUP              chr11  55057761  55057929   
292924     DUP              chr11  55232550  55233450   
292925     DUP              chr11  55240268  55241810   
292926     DUP               chr1  43904745  43905872   
292927     DUP               chr1   1670616  21803665   

                                                     name interval_index  
0                    51658:19412E-Gen001-PCRfree:delly_sv          0:BND  
1               46570:19412AL-Gen005-PCRfree-30X:delly_sv          1:BND  
2               54194:19412RT-Gen005-PCRfree-30X:delly_sv          2:BND  
3                    50708:20487N-Gen001-PCRfree:delly_sv          3:BND  
4                    51659:19412E-Gen001-PCRfree:delly_sv          4:BND  
...                                                   ...            ...  
292923  23336:19412E-Gen001-PCRfree:delly_sv,20183:204...        997:DUP  
292924  33564:19412JR-Gen005-PCRfree-30X:delly_sv,2745...        998:DUP  
292925  23738:20487N-Gen001-PCRfree:delly_sv,19815:204...        999:DUP  
292926                  325:20487-Gen001-PCRfree:delly_sv         99:DUP  
292927                  32:20487A-Gen001-PCRfree:delly_sv          9:DUP  

[292928 rows x 6 columns]

In [22]:
SVs_bed_combined_merged_intervals.index.duplicated().sum()

0

In [23]:
assert SVs_bed_combined_merged_intervals.interval_index.duplicated().sum() == 0

In [27]:
import datetime
date = str(datetime.datetime.now()).replace(" ","_").replace(":","_")
SVs_bed_combined_merged_intervals.to_csv(date+"_"+"SVs_bed_combined_merged_intervals.csv")

<h1> Annotate original data with aggregation results </h1>

In [28]:
SVs_bed_combined_annotated = pd.DataFrame(SVs_bed_combined, copy=True)
SVs_bed_combined_annotated["interval_index"] = pd.NA
assert not any(SVs_bed_combined_annotated["name"].duplicated().values)
SVs_bed_combined_annotated.set_index("name", inplace=True)

In [29]:
def set_interval_index(x):
    items = x["name"].split(",")
    for i in items:
        SVs_bed_combined_annotated.loc[i,"interval_index"] = x.name
_ = SVs_bed_combined_merged_intervals.progress_apply(set_interval_index, axis="columns")

  0%|          | 0/292928 [00:00<?, ?it/s]

In [30]:
assert pd.isna(SVs_bed_combined_annotated["interval_index"]).sum() == 0
SVs_bed_combined_annotated

chrm      start  \
name                                                                         
0:19412RT-Gen005-PCRfree-30X:cue                          chr14   40140613   
1:19412RT-Gen005-PCRfree-30X:cue                          chr14   79639949   
2:19412RT-Gen005-PCRfree-30X:cue                          chr14   35136247   
3:19412RT-Gen005-PCRfree-30X:cue                          chr14   18539053   
4:19412RT-Gen005-PCRfree-30X:cue                          chr14  105906883   
...                                                         ...        ...   
53167:19412AL-Gen005-PCRfree-30X:delly_sv      chrUn_GL000216v2     173813   
53168:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt     742298   
53169:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt    2029973   
53170:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt    1984888   
53171:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt    1984889   

                                                 end SV_type   FILTER  length  \
name                                                                            
0:19412RT-Gen005-PCRfree-30X:cue            40148469     DEL     PASS    7856   
1:19412RT-Gen005-PCRfree-30X:cue            79648707     DEL     PASS    8758   
2:19412RT-Gen005-PCRfree-30X:cue            35145840     DEL     PASS    9593   
3:19412RT-Gen005-PCRfree-30X:cue            18547319     DEL     PASS    8266   
4:19412RT-Gen005-PCRfree-30X:cue           105916674     DEL     PASS    9791   
...                                              ...     ...      ...     ...   
53167:19412AL-Gen005-PCRfree-30X:delly_sv     173814     INV  LowQual       1   
53168:19412AL-Gen005-PCRfree-30X:delly_sv     742299     INV  LowQual       1   
53169:19412AL-Gen005-PCRfree-30X:delly_sv    2029974     INV  LowQual       1   
53170:19412AL-Gen005-PCRfree-30X:delly_sv    1984889     INV     PASS       1   
53171:19412AL-Gen005-PCRfree-30X:delly_sv    1984890     INV     PASS       1   

                                          interval_index  
name                                                      
0:19412RT-Gen005-PCRfree-30X:cue                  210957  
1:19412RT-Gen005-PCRfree-30X:cue                  212524  
2:19412RT-Gen005-PCRfree-30X:cue                  210795  
3:19412RT-Gen005-PCRfree-30X:cue                  210102  
4:19412RT-Gen005-PCRfree-30X:cue                  213783  
...                                                  ...  
53167:19412AL-Gen005-PCRfree-30X:delly_sv         160290  
53168:19412AL-Gen005-PCRfree-30X:delly_sv          90067  
53169:19412AL-Gen005-PCRfree-30X:delly_sv          90069  
53170:19412AL-Gen005-PCRfree-30X:delly_sv          90068  
53171:19412AL-Gen005-PCRfree-30X:delly_sv          90068  

[606505 rows x 7 columns]

In [31]:
SVs_bed_combined_annotated["caller"] = SVs_bed_combined_annotated.index.map(lambda x: x.split(":")[-1])
SVs_bed_combined_annotated["sample"] = SVs_bed_combined_annotated.index.map(lambda x: x.split(":")[1])
SVs_bed_combined_annotated

chrm      start  \
name                                                                         
0:19412RT-Gen005-PCRfree-30X:cue                          chr14   40140613   
1:19412RT-Gen005-PCRfree-30X:cue                          chr14   79639949   
2:19412RT-Gen005-PCRfree-30X:cue                          chr14   35136247   
3:19412RT-Gen005-PCRfree-30X:cue                          chr14   18539053   
4:19412RT-Gen005-PCRfree-30X:cue                          chr14  105906883   
...                                                         ...        ...   
53167:19412AL-Gen005-PCRfree-30X:delly_sv      chrUn_GL000216v2     173813   
53168:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt     742298   
53169:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt    2029973   
53170:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt    1984888   
53171:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt    1984889   

                                                 end SV_type   FILTER  length  \
name                                                                            
0:19412RT-Gen005-PCRfree-30X:cue            40148469     DEL     PASS    7856   
1:19412RT-Gen005-PCRfree-30X:cue            79648707     DEL     PASS    8758   
2:19412RT-Gen005-PCRfree-30X:cue            35145840     DEL     PASS    9593   
3:19412RT-Gen005-PCRfree-30X:cue            18547319     DEL     PASS    8266   
4:19412RT-Gen005-PCRfree-30X:cue           105916674     DEL     PASS    9791   
...                                              ...     ...      ...     ...   
53167:19412AL-Gen005-PCRfree-30X:delly_sv     173814     INV  LowQual       1   
53168:19412AL-Gen005-PCRfree-30X:delly_sv     742299     INV  LowQual       1   
53169:19412AL-Gen005-PCRfree-30X:delly_sv    2029974     INV  LowQual       1   
53170:19412AL-Gen005-PCRfree-30X:delly_sv    1984889     INV     PASS       1   
53171:19412AL-Gen005-PCRfree-30X:delly_sv    1984890     INV     PASS       1   

                                          interval_index    caller  \
name                                                                 
0:19412RT-Gen005-PCRfree-30X:cue                  210957       cue   
1:19412RT-Gen005-PCRfree-30X:cue                  212524       cue   
2:19412RT-Gen005-PCRfree-30X:cue                  210795       cue   
3:19412RT-Gen005-PCRfree-30X:cue                  210102       cue   
4:19412RT-Gen005-PCRfree-30X:cue                  213783       cue   
...                                                  ...       ...   
53167:19412AL-Gen005-PCRfree-30X:delly_sv         160290  delly_sv   
53168:19412AL-Gen005-PCRfree-30X:delly_sv          90067  delly_sv   
53169:19412AL-Gen005-PCRfree-30X:delly_sv          90069  delly_sv   
53170:19412AL-Gen005-PCRfree-30X:delly_sv          90068  delly_sv   
53171:19412AL-Gen005-PCRfree-30X:delly_sv          90068  delly_sv   

                                                               sample  
name                                                                   
0:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X  
1:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X  
2:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X  
3:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X  
4:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X  
...                                                               ...  
53167:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X  
53168:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X  
53169:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X  
53170:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X  
53171:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X  

[606505 rows x 9 columns]

<h1> Regina's data: Group SVs and apply filters </h1>

In [248]:
cases_Regina = ["19412AL", "19412E", "19412JR", "19412RT"]
controls_Regina = ["20487A","20487","20487J","20487N"]

SVs_bed_combined_annotated_Regina = pd.DataFrame(SVs_bed_combined_annotated, copy=True)
SVs_bed_combined_annotated_Regina["sample_short"] = SVs_bed_combined_annotated_Regina["sample"].apply(lambda x: x.split("-")[0])
SVs_bed_combined_annotated_Regina["FILTERbool"] = SVs_bed_combined_annotated_Regina["FILTER"] == "PASS"
SVs_bed_combined_annotated_Regina

chrm      start  \
name                                                                         
0:19412RT-Gen005-PCRfree-30X:cue                          chr14   40140613   
1:19412RT-Gen005-PCRfree-30X:cue                          chr14   79639949   
2:19412RT-Gen005-PCRfree-30X:cue                          chr14   35136247   
3:19412RT-Gen005-PCRfree-30X:cue                          chr14   18539053   
4:19412RT-Gen005-PCRfree-30X:cue                          chr14  105906883   
...                                                         ...        ...   
53167:19412AL-Gen005-PCRfree-30X:delly_sv      chrUn_GL000216v2     173813   
53168:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt     742298   
53169:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt    2029973   
53170:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt    1984888   
53171:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt    1984889   

                                                 end SV_type   FILTER  length  \
name                                                                            
0:19412RT-Gen005-PCRfree-30X:cue            40148469     DEL     PASS    7856   
1:19412RT-Gen005-PCRfree-30X:cue            79648707     DEL     PASS    8758   
2:19412RT-Gen005-PCRfree-30X:cue            35145840     DEL     PASS    9593   
3:19412RT-Gen005-PCRfree-30X:cue            18547319     DEL     PASS    8266   
4:19412RT-Gen005-PCRfree-30X:cue           105916674     DEL     PASS    9791   
...                                              ...     ...      ...     ...   
53167:19412AL-Gen005-PCRfree-30X:delly_sv     173814     INV  LowQual       1   
53168:19412AL-Gen005-PCRfree-30X:delly_sv     742299     INV  LowQual       1   
53169:19412AL-Gen005-PCRfree-30X:delly_sv    2029974     INV  LowQual       1   
53170:19412AL-Gen005-PCRfree-30X:delly_sv    1984889     INV     PASS       1   
53171:19412AL-Gen005-PCRfree-30X:delly_sv    1984890     INV     PASS       1   

                                          interval_index    caller  \
name                                                                 
0:19412RT-Gen005-PCRfree-30X:cue                  210957       cue   
1:19412RT-Gen005-PCRfree-30X:cue                  212524       cue   
2:19412RT-Gen005-PCRfree-30X:cue                  210795       cue   
3:19412RT-Gen005-PCRfree-30X:cue                  210102       cue   
4:19412RT-Gen005-PCRfree-30X:cue                  213783       cue   
...                                                  ...       ...   
53167:19412AL-Gen005-PCRfree-30X:delly_sv         160290  delly_sv   
53168:19412AL-Gen005-PCRfree-30X:delly_sv          90067  delly_sv   
53169:19412AL-Gen005-PCRfree-30X:delly_sv          90069  delly_sv   
53170:19412AL-Gen005-PCRfree-30X:delly_sv          90068  delly_sv   
53171:19412AL-Gen005-PCRfree-30X:delly_sv          90068  delly_sv   

                                                               sample  \
name                                                                    
0:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X   
1:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X   
2:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X   
3:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X   
4:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X   
...                                                               ...   
53167:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X   
53168:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X   
53169:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X   
53170:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X   
53171:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X   

                                          sample_short  FILTERbool  
name                                                        

In [265]:
pv = pd.pivot_table(SVs_bed_combined_annotated_Regina,
               index=["interval_index"],
               columns=["caller","sample_short"],
               values=["FILTERbool"],
               aggfunc=sum
              )
not_found_in_controls = \
    (pd.isna(pv["FILTERbool","delly_sv"][controls_Regina]).sum(axis="columns")==len(controls_Regina)) * \
    (pd.isna(pv["FILTERbool","cue"][controls_Regina]).sum(axis="columns")==len(controls_Regina))

found_in_all_cases_by_any_method = \
    (pd.isna(pv["FILTERbool","delly_sv"][cases_Regina]).sum(axis=1)==0) + \
    (pd.isna(pv["FILTERbool","cue"][cases_Regina]).sum(axis=1)==0)

test = \
 (pd.isna(pv["FILTERbool","delly_sv"][controls_Regina]).sum(axis="columns")==len(controls_Regina))*\
 (pd.isna(pv["FILTERbool","delly_sv"][cases_Regina]).sum(axis=1)==0) + \
 (pd.isna(pv["FILTERbool","cue"][controls_Regina]).sum(axis="columns")==len(controls_Regina))*\
 (pd.isna(pv["FILTERbool","cue"][cases_Regina]).sum(axis=1)==0)

has_pass_flag_in_cases = \
    (pv["FILTERbool","delly_sv"][cases_Regina].fillna(value=0).sum(axis=1)>0) + \
    (pv["FILTERbool","cue"][cases_Regina].fillna(value=0).sum(axis=1)>0)
filt = not_found_in_controls & found_in_all_cases_by_any_method # & has_pass_flag_in_cases
pv[filt]

FILTERbool                                                    \
caller                cue                                                     
sample_short      19412AL 19412E 19412JR 19412RT 20487 20487A 20487J 20487N   
interval_index                                                                
535                   NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
539                   NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
540                   NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
542                   NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
897                   NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
...                   ...    ...     ...     ...   ...    ...    ...    ...   
292085                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
292314                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
292436                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
292634                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
292743                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   

                                                                           
caller         delly_sv                                                    
sample_short    19412AL 19412E 19412JR 19412RT 20487 20487A 20487J 20487N  
interval_index                                                             
535                 2.0    1.0     1.0     1.0   NaN    NaN    NaN    NaN  
539                 0.0    1.0     2.0     2.0   NaN    NaN    NaN    NaN  
540                 0.0    1.0     1.0     1.0   NaN    NaN    NaN    NaN  
542                 0.0    2.0     0.0     0.0   NaN    NaN    NaN    NaN  
897                 0.0    0.0     1.0     1.0   NaN    NaN    NaN    NaN  
...                 ...    ...     ...     ...   ...    ...    ...    ...  
292085              1.0    1.0     0.0     1.0   NaN    NaN    NaN    NaN  
292314              1.0    0.0     1.0     0.0   NaN    NaN    NaN    NaN  
292436              0.0    0.0     0.0     1.0   NaN    NaN    NaN    NaN  
292634              0.0    0.0     0.0     0.0   NaN    NaN    NaN    NaN  
292743              1.0    1.0     1.0     1.0   NaN    NaN    NaN    NaN  

[706 rows x 16 columns]

In [266]:
pv[test]

FILTERbool                                                    \
caller                cue                                                     
sample_short      19412AL 19412E 19412JR 19412RT 20487 20487A 20487J 20487N   
interval_index                                                                
535                   NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
539                   NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
540                   NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
542                   NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
897                   NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
...                   ...    ...     ...     ...   ...    ...    ...    ...   
292085                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
292314                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
292436                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
292634                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
292743                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   

                                                                           
caller         delly_sv                                                    
sample_short    19412AL 19412E 19412JR 19412RT 20487 20487A 20487J 20487N  
interval_index                                                             
535                 2.0    1.0     1.0     1.0   NaN    NaN    NaN    NaN  
539                 0.0    1.0     2.0     2.0   NaN    NaN    NaN    NaN  
540                 0.0    1.0     1.0     1.0   NaN    NaN    NaN    NaN  
542                 0.0    2.0     0.0     0.0   NaN    NaN    NaN    NaN  
897                 0.0    0.0     1.0     1.0   NaN    NaN    NaN    NaN  
...                 ...    ...     ...     ...   ...    ...    ...    ...  
292085              1.0    1.0     0.0     1.0   NaN    NaN    NaN    NaN  
292314              1.0    0.0     1.0     0.0   NaN    NaN    NaN    NaN  
292436              0.0    0.0     0.0     1.0   NaN    NaN    NaN    NaN  
292634              0.0    0.0     0.0     0.0   NaN    NaN    NaN    NaN  
292743              1.0    1.0     1.0     1.0   NaN    NaN    NaN    NaN  

[707 rows x 16 columns]

In [258]:
filtered_Regina = SVs_bed_combined_annotated_Regina\
                        .drop_duplicates(subset="interval_index")\
                        .set_index("interval_index")\
                        .loc[pv[filt].index.values]\
                        .reset_index()

/home/vfishman/miniconda3/envs/jupyter/lib/python3.8/site-packages/pandas/core/indexes/base.py:6982: FutureWarning: In a future version, the Index constructor will not infer numeric dtypes when passed object-dtype sequences (matching Series behavior)
  return Index(sequences[0], name=names)


In [268]:
SVs_bed_combined_annotated_Regina.query("chrm=='chr16' and start==34949786")

chrm     start       end SV_type FILTER  \
name                                                                          
30:19412RT-Gen005-PCRfree-30X:cue  chr16  34949786  34955438     DUP   PASS   

                                   length interval_index caller  \
name                                                              
30:19412RT-Gen005-PCRfree-30X:cue    5652         287539    cue   

                                                       sample sample_short  \
name                                                                         
30:19412RT-Gen005-PCRfree-30X:cue  19412RT-Gen005-PCRfree-30X      19412RT   

                                   FILTERbool  
name                                           
30:19412RT-Gen005-PCRfree-30X:cue        True

In [269]:
filtered_Regina.query("interval_index==287539")

interval_index   chrm     start       end SV_type FILTER  length caller  \
675          287539  chr16  34949786  34955438     DUP   PASS    5652    cue   

                         sample sample_short  FILTERbool  
675  19412RT-Gen005-PCRfree-30X      19412RT        True

<h1>Drafts</h1>

In [536]:
intervals_groupped = SVs_bed_combined_annotated.groupby("interval_index")
intervals_lenFiltered = intervals_groupped.filter(lambda x: len(x)>2)
intervals_lenFiltered

chrm      start  \
name                                                                         
0:19412RT-Gen005-PCRfree-30X:cue                          chr14   40140613   
1:19412RT-Gen005-PCRfree-30X:cue                          chr14   79639949   
2:19412RT-Gen005-PCRfree-30X:cue                          chr14   35136247   
3:19412RT-Gen005-PCRfree-30X:cue                          chr14   18539053   
4:19412RT-Gen005-PCRfree-30X:cue                          chr14  105906883   
...                                                         ...        ...   
53167:19412AL-Gen005-PCRfree-30X:delly_sv      chrUn_GL000216v2     173813   
53168:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt     742298   
53169:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt    2029973   
53170:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt    1984888   
53171:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt    1984889   

                                                 end SV_type  length  \
name                                                                   
0:19412RT-Gen005-PCRfree-30X:cue            40148469     DEL    7856   
1:19412RT-Gen005-PCRfree-30X:cue            79648707     DEL    8758   
2:19412RT-Gen005-PCRfree-30X:cue            35145840     DEL    9593   
3:19412RT-Gen005-PCRfree-30X:cue            18547319     DEL    8266   
4:19412RT-Gen005-PCRfree-30X:cue           105916674     DEL    9791   
...                                              ...     ...     ...   
53167:19412AL-Gen005-PCRfree-30X:delly_sv     173814     INV       1   
53168:19412AL-Gen005-PCRfree-30X:delly_sv     742299     INV       1   
53169:19412AL-Gen005-PCRfree-30X:delly_sv    2029974     INV       1   
53170:19412AL-Gen005-PCRfree-30X:delly_sv    1984889     INV       1   
53171:19412AL-Gen005-PCRfree-30X:delly_sv    1984890     INV       1   

                                          interval_index    caller  \
name                                                                 
0:19412RT-Gen005-PCRfree-30X:cue                  210957       cue   
1:19412RT-Gen005-PCRfree-30X:cue                  212524       cue   
2:19412RT-Gen005-PCRfree-30X:cue                  210795       cue   
3:19412RT-Gen005-PCRfree-30X:cue                  210102       cue   
4:19412RT-Gen005-PCRfree-30X:cue                  213783       cue   
...                                                  ...       ...   
53167:19412AL-Gen005-PCRfree-30X:delly_sv         160290  delly_sv   
53168:19412AL-Gen005-PCRfree-30X:delly_sv          90067  delly_sv   
53169:19412AL-Gen005-PCRfree-30X:delly_sv          90069  delly_sv   
53170:19412AL-Gen005-PCRfree-30X:delly_sv          90068  delly_sv   
53171:19412AL-Gen005-PCRfree-30X:delly_sv          90068  delly_sv   

                                                               sample  is_case  
name                                                                            
0:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X     True  
1:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X     True  
2:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X     True  
3:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X     True  
4:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X     True  
...                                                               ...      ...  
53167:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  
53168:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  
53169:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  
53170:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  
53171:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  

[303703 rows x 9 columns]

In [537]:
intervals_lenFiltered.drop_duplicates(subset=["caller","sample","interval_index"], inplace=True)
intervals_lenFiltered

chrm      start  \
name                                                                         
0:19412RT-Gen005-PCRfree-30X:cue                          chr14   40140613   
1:19412RT-Gen005-PCRfree-30X:cue                          chr14   79639949   
2:19412RT-Gen005-PCRfree-30X:cue                          chr14   35136247   
3:19412RT-Gen005-PCRfree-30X:cue                          chr14   18539053   
4:19412RT-Gen005-PCRfree-30X:cue                          chr14  105906883   
...                                                         ...        ...   
53149:19412AL-Gen005-PCRfree-30X:delly_sv      chrUn_GL000216v2     167824   
53156:19412AL-Gen005-PCRfree-30X:delly_sv      chrUn_GL000216v2     169955   
53167:19412AL-Gen005-PCRfree-30X:delly_sv      chrUn_GL000216v2     173813   
53169:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt    2029973   
53170:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt    1984888   

                                                 end SV_type  length  \
name                                                                   
0:19412RT-Gen005-PCRfree-30X:cue            40148469     DEL    7856   
1:19412RT-Gen005-PCRfree-30X:cue            79648707     DEL    8758   
2:19412RT-Gen005-PCRfree-30X:cue            35145840     DEL    9593   
3:19412RT-Gen005-PCRfree-30X:cue            18547319     DEL    8266   
4:19412RT-Gen005-PCRfree-30X:cue           105916674     DEL    9791   
...                                              ...     ...     ...   
53149:19412AL-Gen005-PCRfree-30X:delly_sv     167825     INV       1   
53156:19412AL-Gen005-PCRfree-30X:delly_sv     169956     INV       1   
53167:19412AL-Gen005-PCRfree-30X:delly_sv     173814     INV       1   
53169:19412AL-Gen005-PCRfree-30X:delly_sv    2029974     INV       1   
53170:19412AL-Gen005-PCRfree-30X:delly_sv    1984889     INV       1   

                                          interval_index    caller  \
name                                                                 
0:19412RT-Gen005-PCRfree-30X:cue                  210957       cue   
1:19412RT-Gen005-PCRfree-30X:cue                  212524       cue   
2:19412RT-Gen005-PCRfree-30X:cue                  210795       cue   
3:19412RT-Gen005-PCRfree-30X:cue                  210102       cue   
4:19412RT-Gen005-PCRfree-30X:cue                  213783       cue   
...                                                  ...       ...   
53149:19412AL-Gen005-PCRfree-30X:delly_sv         160287  delly_sv   
53156:19412AL-Gen005-PCRfree-30X:delly_sv         160289  delly_sv   
53167:19412AL-Gen005-PCRfree-30X:delly_sv         160290  delly_sv   
53169:19412AL-Gen005-PCRfree-30X:delly_sv          90069  delly_sv   
53170:19412AL-Gen005-PCRfree-30X:delly_sv          90068  delly_sv   

                                                               sample  is_case  
name                                                                            
0:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X     True  
1:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X     True  
2:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X     True  
3:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X     True  
4:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X     True  
...                                                               ...      ...  
53149:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  
53156:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  
53167:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  
53169:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  
53170:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  

[171969 rows x 9 columns]

In [538]:
intervals_lenFiltered.query("SV_type in @BND_types")#.value_counts() #.groupby("interval_index").get_group(500)

chrm     start  \
name                                                                        
272:19412RT-Gen005-PCRfree-30X:cue                        chr14  68441932   
273:19412RT-Gen005-PCRfree-30X:cue                        chr19  23379892   
274:19412RT-Gen005-PCRfree-30X:cue                        chr19  14396476   
275:19412RT-Gen005-PCRfree-30X:cue                        chr19  21650628   
277:19412RT-Gen005-PCRfree-30X:cue                        chr19  15675571   
...                                                         ...       ...   
53149:19412AL-Gen005-PCRfree-30X:delly_sv      chrUn_GL000216v2    167824   
53156:19412AL-Gen005-PCRfree-30X:delly_sv      chrUn_GL000216v2    169955   
53167:19412AL-Gen005-PCRfree-30X:delly_sv      chrUn_GL000216v2    173813   
53169:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt   2029973   
53170:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt   1984888   

                                                end SV_type  length  \
name                                                                  
272:19412RT-Gen005-PCRfree-30X:cue         68441933     INV       1   
273:19412RT-Gen005-PCRfree-30X:cue         23379893     INV       1   
274:19412RT-Gen005-PCRfree-30X:cue         14396477     INV       1   
275:19412RT-Gen005-PCRfree-30X:cue         21650629     INV       1   
277:19412RT-Gen005-PCRfree-30X:cue         15675572     INV       1   
...                                             ...     ...     ...   
53149:19412AL-Gen005-PCRfree-30X:delly_sv    167825     INV       1   
53156:19412AL-Gen005-PCRfree-30X:delly_sv    169956     INV       1   
53167:19412AL-Gen005-PCRfree-30X:delly_sv    173814     INV       1   
53169:19412AL-Gen005-PCRfree-30X:delly_sv   2029974     INV       1   
53170:19412AL-Gen005-PCRfree-30X:delly_sv   1984889     INV       1   

                                          interval_index    caller  \
name                                                                 
272:19412RT-Gen005-PCRfree-30X:cue                 81559       cue   
273:19412RT-Gen005-PCRfree-30X:cue                 98369       cue   
274:19412RT-Gen005-PCRfree-30X:cue                 97833       cue   
275:19412RT-Gen005-PCRfree-30X:cue                 98255       cue   
277:19412RT-Gen005-PCRfree-30X:cue                 97905       cue   
...                                                  ...       ...   
53149:19412AL-Gen005-PCRfree-30X:delly_sv         160287  delly_sv   
53156:19412AL-Gen005-PCRfree-30X:delly_sv         160289  delly_sv   
53167:19412AL-Gen005-PCRfree-30X:delly_sv         160290  delly_sv   
53169:19412AL-Gen005-PCRfree-30X:delly_sv          90069  delly_sv   
53170:19412AL-Gen005-PCRfree-30X:delly_sv          90068  delly_sv   

                                                               sample  is_case  
name                                                                            
272:19412RT-Gen005-PCRfree-30X:cue         19412RT-Gen005-PCRfree-30X     True  
273:19412RT-Gen005-PCRfree-30X:cue         19412RT-Gen005-PCRfree-30X     True  
274:19412RT-Gen005-PCRfree-30X:cue         19412RT-Gen005-PCRfree-30X     True  
275:19412RT-Gen005-PCRfree-30X:cue         19412RT-Gen005-PCRfree-30X     True  
277:19412RT-Gen005-PCRfree-30X:cue         19412RT-Gen005-PCRfree-30X     True  
...                                                               ...      ...  
53149:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  
53156:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  
53167:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  
53169:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  
53170:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  

[95025 rows x 9 columns]

In [539]:
intervals_lenFiltered.groupby("interval_index").get_group(90068).iloc[0]["SV_type"] in BND_types

True

In [540]:
def f(x):
    is_BND = x.iloc[0]["SV_type"] in BND_types
        
    x = x.groupby(["caller","is_case"])["chrm"].agg(len)

    result_cue = \
            x.get(("cue",True), 0) == len(cases) and \
            x.get(("cue",False), 0) == 0
    result_delly_sv = \
            x.get(("delly_sv",True), 0) == len(cases) and \
            x.get(("delly_sv",False), 0) == 0

    if is_BND:
        return result_cue or result_delly_sv
    else:
        return result_cue or result_delly_sv

filtered = intervals_lenFiltered.groupby("interval_index").filter(f)
filtered 

chrm      start        end  \
name                                                                     
30:19412RT-Gen005-PCRfree-30X:cue          chr16   34949786   34955438   
90:19412RT-Gen005-PCRfree-30X:cue          chr10   20560725   20572097   
143:19412RT-Gen005-PCRfree-30X:cue          chr6   54063913   54070031   
148:19412RT-Gen005-PCRfree-30X:cue          chr6   66298839   66339024   
156:19412RT-Gen005-PCRfree-30X:cue          chr6   65001119   65005820   
...                                          ...        ...        ...   
51773:19412AL-Gen005-PCRfree-30X:delly_sv  chr11    5920639    5920640   
51950:19412AL-Gen005-PCRfree-30X:delly_sv  chr13   87187987   87187988   
51960:19412AL-Gen005-PCRfree-30X:delly_sv  chr13  112397803  112397804   
52138:19412AL-Gen005-PCRfree-30X:delly_sv  chr16   46415747   46415748   
52764:19412AL-Gen005-PCRfree-30X:delly_sv   chrY   11643791   11643792   

                                          SV_type  length interval_index  \
name                                                                       
30:19412RT-Gen005-PCRfree-30X:cue             DUP    5652         287539   
90:19412RT-Gen005-PCRfree-30X:cue             DEL   11372         173162   
143:19412RT-Gen005-PCRfree-30X:cue            DEL    6118         281798   
148:19412RT-Gen005-PCRfree-30X:cue            DEL   40185         282228   
156:19412RT-Gen005-PCRfree-30X:cue            DEL    4701         282207   
...                                           ...     ...            ...   
51773:19412AL-Gen005-PCRfree-30X:delly_sv     INV       1          65812   
51950:19412AL-Gen005-PCRfree-30X:delly_sv     INV       1          78822   
51960:19412AL-Gen005-PCRfree-30X:delly_sv     INV       1          79633   
52138:19412AL-Gen005-PCRfree-30X:delly_sv     INV       1          88263   
52764:19412AL-Gen005-PCRfree-30X:delly_sv     INV       1         164000   

                                             caller  \
name                                                  
30:19412RT-Gen005-PCRfree-30X:cue               cue   
90:19412RT-Gen005-PCRfree-30X:cue               cue   
143:19412RT-Gen005-PCRfree-30X:cue              cue   
148:19412RT-Gen005-PCRfree-30X:cue              cue   
156:19412RT-Gen005-PCRfree-30X:cue              cue   
...                                             ...   
51773:19412AL-Gen005-PCRfree-30X:delly_sv  delly_sv   
51950:19412AL-Gen005-PCRfree-30X:delly_sv  delly_sv   
51960:19412AL-Gen005-PCRfree-30X:delly_sv  delly_sv   
52138:19412AL-Gen005-PCRfree-30X:delly_sv  delly_sv   
52764:19412AL-Gen005-PCRfree-30X:delly_sv  delly_sv   

                                                               sample  is_case  
name                                                                            
30:19412RT-Gen005-PCRfree-30X:cue          19412RT-Gen005-PCRfree-30X     True  
90:19412RT-Gen005-PCRfree-30X:cue          19412RT-Gen005-PCRfree-30X     True  
143:19412RT-Gen005-PCRfree-30X:cue         19412RT-Gen005-PCRfree-30X     True  
148:19412RT-Gen005-PCRfree-30X:cue         19412RT-Gen005-PCRfree-30X     True  
156:19412RT-Gen005-PCRfree-30X:cue         19412RT-Gen005-PCRfree-30X     True  
...                                                               ...      ...  
51773:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  
51950:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  
51960:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  
52138:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  
52764:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True  

[2872 rows x 9 columns]

In [518]:
# filtered.sort_values(by=["interval_index"])
filtered.drop_duplicates(subset=["interval_index"])#.query("SV_type in @BND_types").sort_values(by=["chrm","start"])

chrm      start        end  \
name                                                                     
30:19412RT-Gen005-PCRfree-30X:cue          chr16   34949786   34955438   
90:19412RT-Gen005-PCRfree-30X:cue          chr10   20560725   20572097   
143:19412RT-Gen005-PCRfree-30X:cue          chr6   54063913   54070031   
148:19412RT-Gen005-PCRfree-30X:cue          chr6   66298839   66339024   
156:19412RT-Gen005-PCRfree-30X:cue          chr6   65001119   65005820   
...                                          ...        ...        ...   
60406:19412RT-Gen005-PCRfree-30X:delly_sv  chr13  112397990  112397991   
60533:19412RT-Gen005-PCRfree-30X:delly_sv  chr16   36188622   36188623   
60606:19412RT-Gen005-PCRfree-30X:delly_sv  chr16   46415784   46415785   
60982:19412RT-Gen005-PCRfree-30X:delly_sv  chr20   29495283   29495284   
61197:19412RT-Gen005-PCRfree-30X:delly_sv   chrY   11643794   11643795   

                                          SV_type  length interval_index  \
name                                                                       
30:19412RT-Gen005-PCRfree-30X:cue             DUP    5652         287539   
90:19412RT-Gen005-PCRfree-30X:cue             DEL   11372         173162   
143:19412RT-Gen005-PCRfree-30X:cue            DEL    6118         281798   
148:19412RT-Gen005-PCRfree-30X:cue            DEL   40185         282228   
156:19412RT-Gen005-PCRfree-30X:cue            DEL    4701         282207   
...                                           ...     ...            ...   
60406:19412RT-Gen005-PCRfree-30X:delly_sv     INV       1          79633   
60533:19412RT-Gen005-PCRfree-30X:delly_sv     INV       1          88185   
60606:19412RT-Gen005-PCRfree-30X:delly_sv     INV       1          88263   
60982:19412RT-Gen005-PCRfree-30X:delly_sv     INV       1         111924   
61197:19412RT-Gen005-PCRfree-30X:delly_sv     INV       1         164000   

                                             caller  \
name                                                  
30:19412RT-Gen005-PCRfree-30X:cue               cue   
90:19412RT-Gen005-PCRfree-30X:cue               cue   
143:19412RT-Gen005-PCRfree-30X:cue              cue   
148:19412RT-Gen005-PCRfree-30X:cue              cue   
156:19412RT-Gen005-PCRfree-30X:cue              cue   
...                                             ...   
60406:19412RT-Gen005-PCRfree-30X:delly_sv  delly_sv   
60533:19412RT-Gen005-PCRfree-30X:delly_sv  delly_sv   
60606:19412RT-Gen005-PCRfree-30X:delly_sv  delly_sv   
60982:19412RT-Gen005-PCRfree-30X:delly_sv  delly_sv   
61197:19412RT-Gen005-PCRfree-30X:delly_sv  delly_sv   

                                                               sample  is_case  
name                                                                            
30:19412RT-Gen005-PCRfree-30X:cue          19412RT-Gen005-PCRfree-30X     True  
90:19412RT-Gen005-PCRfree-30X:cue          19412RT-Gen005-PCRfree-30X     True  
143:19412RT-Gen005-PCRfree-30X:cue         19412RT-Gen005-PCRfree-30X     True  
148:19412RT-Gen005-PCRfree-30X:cue         19412RT-Gen005-PCRfree-30X     True  
156:19412RT-Gen005-PCRfree-30X:cue         19412RT-Gen005-PCRfree-30X     True  
...                                                               ...      ...  
60406:19412RT-Gen005-PCRfree-30X:delly_sv  19412RT-Gen005-PCRfree-30X     True  
60533:19412RT-Gen005-PCRfree-30X:delly_sv  19412RT-Gen005-PCRfree-30X     True  
60606:19412RT-Gen005-PCRfree-30X:delly_sv  19412RT-Gen005-PCRfree-30X     True  
60982:19412RT-Gen005-PCRfree-30X:delly_sv  19412RT-Gen005-PCRfree-30X     True  
61197:19412RT-Gen005-PCRfree-30X:delly_sv  19412RT-Gen005-PCRfree-30X     True  

[707 rows x 9 columns]

In [541]:
filtered.drop_duplicates(subset=["interval_index"]).query("chrm=='chr6'")

chrm      start        end SV_type  \
name                                                                            
143:19412RT-Gen005-PCRfree-30X:cue         chr6   54063913   54070031     DEL   
148:19412RT-Gen005-PCRfree-30X:cue         chr6   66298839   66339024     DEL   
156:19412RT-Gen005-PCRfree-30X:cue         chr6   65001119   65005820     DEL   
15285:19412RT-Gen005-PCRfree-30X:delly_sv  chr6     857169     857384     DEL   
15349:19412RT-Gen005-PCRfree-30X:delly_sv  chr6    5656562    5656563     INS   
15508:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   17276218   17276245     DEL   
15537:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   18622583   18622611     DEL   
15545:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   19049142   19049181     DEL   
15547:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   19155400   19155736     DEL   
15549:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   19224251   19250151     DUP   
15550:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   19334912   19334974     DEL   
15595:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   22508532   22508533     BND   
15645:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   26436606   26436636     DEL   
15676:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   29619658   29619687     DEL   
15678:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   29633966   29633997     DEL   
15717:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   31397451   31397452     BND   
15753:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   32783244   32783306     DEL   
15763:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   33158143   33159064     DEL   
15931:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   44645747   44646064     DEL   
16021:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   51334674   51335325     DEL   
16065:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   54059857   54063910     DUP   
16066:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   54060005   54070031     DEL   
16165:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   60242552   60242553     BND   
16242:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   63480956   63480993     DEL   
16253:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   64475259   64475574     DEL   
16291:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   67232742   67232898     DEL   
16319:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   69532251   69532280     DEL   
16332:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   71508487   71508519     DEL   
16373:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   74223009   74223351     DEL   
16399:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   76320832   76320859     DEL   
16426:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   78738009   78738010     BND   
16452:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   81435165   81469532     DUP   
16534:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   87997898   87997899     BND   
16547:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   89052054   89055450     DUP   
16603:19412RT-Gen005-PCRfree-30X:delly_sv  chr6   95432547   95432585     DEL   
16722:19412RT-Gen005-PCRfree-30X:delly_sv  chr6  105909607  105909663     DEL   
16799:19412RT-Gen005-PCRfree-30X:delly_sv  chr6  111303671  111303720     DEL   
16881:19412RT-Gen005-PCRfree-30X:delly_sv  chr6  120519513  120519514     BND   
16897:19412RT-Gen005-PCRfree-30X:delly_sv  chr6  122102273  122102300     DEL   
16914:19412RT-Gen005-PCRfree-30X:delly_sv  chr6  123530326  123530354     DEL   
16919:19412RT-Gen005-PCRfree-30X:delly_sv  chr6  123937988  123937989     INS   
17002:19412RT-Gen005-PCRfree-30X:delly_sv  chr6  133616902  133616931     DEL   
17105:19412RT-Gen005-PCRfree-30X:delly_sv  chr6  145497526  145497625     DEL   
17120:19412RT-Gen005-PCRfree-30X:delly_sv  chr6  148251820  148251821     BND   
17249:19412RT-Gen005-PCRfree-30X:delly_sv  chr6  158414414  158414415     INS   
17260:19412RT-Gen005-PCRfree-30X:delly_sv  chr6  159231077  159231391     DEL   
17301:19412RT-Gen005-PCRfree-30X:delly_sv  chr6  162838730  162838731     BND   
17307:19412RT-Gen005-PCRfree-30X:delly_sv  chr6  163319487  163319516     

In [542]:
len(filtered.drop_duplicates(subset=["interval_index"]).query("chrm=='chr6'"))

51

<h1>Regina's data: Genes filter</h1>

In [259]:
genes = pd.read_csv("Deafnes_genes_mart_export.tsv", sep="\t")
genes["chrm"] = genes["Chromosome/scaffold name"].apply(lambda x: "chr" + x)
genes

Gene stable ID Gene stable ID version Chromosome/scaffold name  \
0    ENSG00000006611     ENSG00000006611.17                       11   
1    ENSG00000010165     ENSG00000010165.20                        1   
2    ENSG00000019991     ENSG00000019991.18                        7   
3    ENSG00000041982     ENSG00000041982.17                        9   
4    ENSG00000042781     ENSG00000042781.14                        1   
..               ...                    ...                      ...   
139  ENSG00000215203      ENSG00000215203.3                        4   
140  ENSG00000242866     ENSG00000242866.10                       15   
141  ENSG00000249581      ENSG00000249581.2                        4   
142  ENSG00000267534      ENSG00000267534.4                       19   
143  ENSG00000284922      ENSG00000284922.2                       11   

     Gene start (bp)  Gene end (bp) Gene name   chrm  
0           17493895       17544416     USH1C  chr11  
1          171781660      171814023   METTL13   chr1  
2           81699010       81770438       HGF   chr7  
3          115019575      115118207       TNC   chr9  
4          215622891      216423448     USH2A   chr1  
..               ...            ...       ...    ...  
139         42892713       43030658    GRXCR1   chr4  
140         43599563       43618800      STRC  chr15  
141         17515165       17527104     CLRN2   chr4  
142         10221433       10231331     S1PR2  chr19  
143         72080331       72110782    LRTOMT  chr11  

[144 rows x 7 columns]

In [260]:
genes_bt = pybedtools.BedTool.from_dataframe(
        genes[["chrm","Gene start (bp)","Gene end (bp)","Gene name"]]).sort()
genes_bt
filtered_SV_bt = pybedtools.BedTool.from_dataframe(
        filtered_Regina.drop_duplicates(subset=["interval_index"])[
                ["chrm","start","end","interval_index","SV_type","length","caller"]
    ]).sort()

/home/vfishman/miniconda3/envs/jupyter/lib/python3.8/subprocess.py:849: RuntimeWarning: line buffering (buffering=1) isn't supported in binary mode, the default buffer size will be used
  self.stderr = io.open(errread, 'rb', bufsize)
/home/vfishman/miniconda3/envs/jupyter/lib/python3.8/subprocess.py:849: RuntimeWarning: line buffering (buffering=1) isn't supported in binary mode, the default buffer size will be used
  self.stderr = io.open(errread, 'rb', bufsize)


In [263]:
filtered_SV_with_closest_genes = filtered_SV_bt.closest(genes_bt,d=True)
filtered_SV_with_closest_genes.to_dataframe().\
                                rename(columns={
                                    "name":"interval_index",
                                    "score":"SV_type",
                                    "strand":"SV_len",
                                    "thickStart":"caller",
                                    "thickEnd":"geneChr",
                                    "itemRgb":"geneStart",
                                    "blockCount":"geneEnd",
                                    "blockSizes":"geneName",
                                    "blockStarts":"SV_distance"
                                }).\
                                query("SV_distance>=0").\
                                sort_values(by=["SV_distance"])
#                                query("blockStarts>0 and chrom=='chr6'").\


/home/vfishman/miniconda3/envs/jupyter/lib/python3.8/subprocess.py:849: RuntimeWarning: line buffering (buffering=1) isn't supported in binary mode, the default buffer size will be used
  self.stderr = io.open(errread, 'rb', bufsize)
***** WARNING: File /tmp/pybedtools.bm9cly8h.tmp has inconsistent naming convention for record:
chr1	6424776	6461367	ESPN

***** WARNING: File /tmp/pybedtools.bm9cly8h.tmp has inconsistent naming convention for record:
chr1	6424776	6461367	ESPN



chrom      start        end  interval_index SV_type  SV_len    caller  \
208  chr15   51605504   51605844          215663     DEL     340  delly_sv   
375   chr3   10540629   10540630           25242     BND       1  delly_sv   
93   chr11  110006623  110006650          198581     DEL      27  delly_sv   
207  chr15   43176051   43650318          287360     DUP  474267  delly_sv   
118  chr12   80220579   80220756          204153     DEL     177  delly_sv   
..     ...        ...        ...             ...     ...     ...       ...   
614   chr9    1805194    1805195           40298     BND       1  delly_sv   
585   chr8   25191906   25191907           38332     BND       1  delly_sv   
584   chr8   24374462   24374497          172397     DEL      35  delly_sv   
583   chr8   23348073   23348074           38296     BND       1  delly_sv   
582   chr8   18593999   18594000           38213     BND       1  delly_sv   

    geneChr  geneStart    geneEnd geneName  SV_distance  
208   chr15   51447711   51622833    DMXL2            0  
375    chr3   10324023   10708007   ATP2B2            0  
93    chr11  109864295  110296712      RDX            0  
207   chr15   43599563   43618800     STRC            0  
118   chr12   80099537   80380880    OTOGL            0  
..      ...        ...        ...      ...          ...  
614    chr9   69121264   69274615     TJP2     67316070  
585    chr8   94641074   94707466    ESRP1     69449168  
584    chr8   94641074   94707466    ESRP1     70266578  
583    chr8   94641074   94707466    ESRP1     71293001  
582    chr8   94641074   94707466    ESRP1     76047075  

[641 rows x 12 columns]

In [255]:
SVs_bed_combined_annotated_Regina.query("interval_index==287360")

chrm     start       end SV_type  \
name                                                                           
35683:19412RT-Gen005-PCRfree-30X:delly_sv  chr15  43176051  43650318     DUP   
30750:19412E-Gen001-PCRfree:delly_sv       chr15  43176060  43650269     DUP   
43466:19412JR-Gen005-PCRfree-30X:delly_sv  chr15  43176040  43650068     DUP   
30284:19412AL-Gen005-PCRfree-30X:delly_sv  chr15  43176040  43650355     DUP   

                                            FILTER  length interval_index  \
name                                                                        
35683:19412RT-Gen005-PCRfree-30X:delly_sv     PASS  474267         287360   
30750:19412E-Gen001-PCRfree:delly_sv       LowQual  474209         287360   
43466:19412JR-Gen005-PCRfree-30X:delly_sv  LowQual  474028         287360   
30284:19412AL-Gen005-PCRfree-30X:delly_sv  LowQual  474315         287360   

                                             caller  \
name                                                  
35683:19412RT-Gen005-PCRfree-30X:delly_sv  delly_sv   
30750:19412E-Gen001-PCRfree:delly_sv       delly_sv   
43466:19412JR-Gen005-PCRfree-30X:delly_sv  delly_sv   
30284:19412AL-Gen005-PCRfree-30X:delly_sv  delly_sv   

                                                               sample  \
name                                                                    
35683:19412RT-Gen005-PCRfree-30X:delly_sv  19412RT-Gen005-PCRfree-30X   
30750:19412E-Gen001-PCRfree:delly_sv            19412E-Gen001-PCRfree   
43466:19412JR-Gen005-PCRfree-30X:delly_sv  19412JR-Gen005-PCRfree-30X   
30284:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X   

                                          sample_short  FILTERbool  
name                                                                
35683:19412RT-Gen005-PCRfree-30X:delly_sv      19412RT        True  
30750:19412E-Gen001-PCRfree:delly_sv            19412E       False  
43466:19412JR-Gen005-PCRfree-30X:delly_sv      19412JR       False  
30284:19412AL-Gen005-PCRfree-30X:delly_sv      19412AL       False

In [497]:
filtered_SV_with_closest_genes.to_dataframe().score.value_counts()

BND    221
INV     43
INS     24
DEL      6
DUP      1
Name: score, dtype: int64

In [491]:
SVs_bed_combined_merged_intervals.iloc[50869]

SV_type                                                         INS
chrom                                                          chr9
start                                                      69095657
end                                                        69095658
name              22670:19412RT-Gen005-PCRfree-30X:delly_sv,1986...
interval_index                                             2591:INS
Name: 50869, dtype: object

In [492]:
SVs_bed_combined_annotated.query("interval_index==50869")

chrm     start       end SV_type  \
name                                                                          
22670:19412RT-Gen005-PCRfree-30X:delly_sv  chr9  69095657  69095658     INS   
19316:19412E-Gen001-PCRfree:delly_sv       chr9  69095657  69095658     INS   
28152:19412JR-Gen005-PCRfree-30X:delly_sv  chr9  69095657  69095658     INS   
19862:19412AL-Gen005-PCRfree-30X:delly_sv  chr9  69095657  69095658     INS   

                                           length interval_index    caller  \
name                                                                         
22670:19412RT-Gen005-PCRfree-30X:delly_sv       1          50869  delly_sv   
19316:19412E-Gen001-PCRfree:delly_sv            1          50869  delly_sv   
28152:19412JR-Gen005-PCRfree-30X:delly_sv       1          50869  delly_sv   
19862:19412AL-Gen005-PCRfree-30X:delly_sv       1          50869  delly_sv   

                                                               sample  is_case  
name                                                                            
22670:19412RT-Gen005-PCRfree-30X:delly_sv  19412RT-Gen005-PCRfree-30X     True  
19316:19412E-Gen001-PCRfree:delly_sv            19412E-Gen001-PCRfree     True  
28152:19412JR-Gen005-PCRfree-30X:delly_sv  19412JR-Gen005-PCRfree-30X     True  
19862:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X     True

In [493]:
!grep -e "69095657" /home/vfishman/projects/regina_deafness/19412RT-Gen005-PCRfree-30X/delly/delly.sv.vcf | grep -e "chr9" | head -3

chr9	69095657	INS00024743	A	<INS>	600	PASS	PRECISE;SVTYPE=INS;SVMETHOD=EMBL.DELLYv1.1.6;END=69095658;SVLEN=37;PE=0;MAPQ=0;CT=NtoN;CIPOS=-12,12;CIEND=-12,12;SRMAPQ=60;INSLEN=37;HOMLEN=13;SR=10;SRQ=1;CONSENSUS=ATGACAAATAATATCACAGAGTGTACACCCACTGTGATGTTAGGAGTAATACCTCCCTATGATATTACAAAAATATTACAGTGTGTACACACACTGTGATATTACAAGTAATACTGCCTTTAGATACTACAAATAATATCACAGGGTGTACATCTACTGTGATATTAGGAG;CE=1.91742	GT:GL:GQ:FT:RCL:RC:RCR:RDCN:DR:DV:RR:RV	1/1:-179.165,-18.3283,0:10000:PASS:11411:27679:16268:2:0:0:0:61


In [434]:
x = intervals_groupped.\
            get_group(286781).\
            drop_duplicates(subset=["caller","sample"]).\
            groupby(["caller","is_case"]).\
            agg(len)["chrm"].\
            get(("cue",True), 0)
x
#x.loc[("cue",True),"chrm"]

0

In [395]:
intervals_groupped.get_group(286781)

chrm      start        end SV_type  \
name                                                                           
972:19412RT-Gen005-PCRfree-30X:delly_sv   chr1  121750412  124250799     DUP   
975:19412RT-Gen005-PCRfree-30X:delly_sv   chr1  121751354  122599321     DUP   
976:19412RT-Gen005-PCRfree-30X:delly_sv   chr1  121751360  123654392     DUP   
983:19412RT-Gen005-PCRfree-30X:delly_sv   chr1  121762979  123603640     DUP   
986:19412RT-Gen005-PCRfree-30X:delly_sv   chr1  121771584  123001486     DUP   
...                                        ...        ...        ...     ...   
3408:19412AL-Gen005-PCRfree-30X:delly_sv  chr1  124679191  124741535     DUP   
3409:19412AL-Gen005-PCRfree-30X:delly_sv  chr1  124679202  124757789     DUP   
3410:19412AL-Gen005-PCRfree-30X:delly_sv  chr1  124690488  124757784     DUP   
3411:19412AL-Gen005-PCRfree-30X:delly_sv  chr1  124699448  124757784     DUP   
3415:19412AL-Gen005-PCRfree-30X:delly_sv  chr1  124731161  124757790     DUP   

                                           length interval_index  
name                                                              
972:19412RT-Gen005-PCRfree-30X:delly_sv   2500387         286781  
975:19412RT-Gen005-PCRfree-30X:delly_sv    847967         286781  
976:19412RT-Gen005-PCRfree-30X:delly_sv   1903032         286781  
983:19412RT-Gen005-PCRfree-30X:delly_sv   1840661         286781  
986:19412RT-Gen005-PCRfree-30X:delly_sv   1229902         286781  
...                                           ...            ...  
3408:19412AL-Gen005-PCRfree-30X:delly_sv    62344         286781  
3409:19412AL-Gen005-PCRfree-30X:delly_sv    78587         286781  
3410:19412AL-Gen005-PCRfree-30X:delly_sv    67296         286781  
3411:19412AL-Gen005-PCRfree-30X:delly_sv    58336         286781  
3415:19412AL-Gen005-PCRfree-30X:delly_sv    26629         286781  

[5509 rows x 6 columns]

In [404]:
!grep -e "12175" /home/vfishman/projects/regina_deafness/19412RT-Gen005-PCRfree-30X/delly/delly.sv.vcf | grep -e "chr1" | head -3

chr1	121750412	DUP00001055	C	<DUP>	6	LowQual	IMPRECISE;SVTYPE=DUP;SVMETHOD=EMBL.DELLYv1.1.6;END=124250799;PE=2;MAPQ=5;CT=5to3;CIPOS=-902,902;CIEND=-902,902	GT:GL:GQ:FT:RCL:RC:RCR:RDCN:DR:DV:RR:RV	0/0:0,-135.537,-1000:10000:PASS:81880:331890:269459:2:494:1:0:0
chr1	121750635	DEL00001056	C	<DEL>	10	LowQual	IMPRECISE;SVTYPE=DEL;SVMETHOD=EMBL.DELLYv1.1.6;END=123443337;PE=2;MAPQ=5;CT=3to5;CIPOS=-876,876;CIEND=-876,876	GT:GL:GQ:FT:RCL:RC:RCR:RDCN:DR:DV:RR:RV	0/0:0,-6.36486,-30.9641:64:PASS:60235:177711:161989:2:28:2:0:0
chr1	121750646	DEL00001057	A	<DEL>	12	LowQual	IMPRECISE;SVTYPE=DEL;SVMETHOD=EMBL.DELLYv1.1.6;END=124250659;PE=6;MAPQ=2;CT=3to5;CIPOS=-882,882;CIEND=-882,882	GT:GL:GQ:FT:RCL:RC:RCR:RDCN:DR:DV:RR:RV	0/0:0,-66.3729,-556.121:10000:PASS:82112:330206:270893:2:245:0:0:0


<h1>Ana's cases</h1>

In [190]:
controls_Ana = ["19412AL", "19412E", "19412JR", "19412RT","20487J","20487A"]
cases_Ana = ["20487","20487N"]

SVs_bed_combined_annotated_Ana = pd.DataFrame(SVs_bed_combined_annotated, copy=True)
SVs_bed_combined_annotated_Ana["sample_short"] = SVs_bed_combined_annotated_Ana["sample"].apply(lambda x: x.split("-")[0])
SVs_bed_combined_annotated_Ana["FILTERbool"] = SVs_bed_combined_annotated_Ana["FILTER"] == "PASS"
SVs_bed_combined_annotated_Ana

chrm      start  \
name                                                                         
0:19412RT-Gen005-PCRfree-30X:cue                          chr14   40140613   
1:19412RT-Gen005-PCRfree-30X:cue                          chr14   79639949   
2:19412RT-Gen005-PCRfree-30X:cue                          chr14   35136247   
3:19412RT-Gen005-PCRfree-30X:cue                          chr14   18539053   
4:19412RT-Gen005-PCRfree-30X:cue                          chr14  105906883   
...                                                         ...        ...   
53167:19412AL-Gen005-PCRfree-30X:delly_sv      chrUn_GL000216v2     173813   
53168:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt     742298   
53169:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt    2029973   
53170:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt    1984888   
53171:19412AL-Gen005-PCRfree-30X:delly_sv  chr16_KI270853v1_alt    1984889   

                                                 end SV_type   FILTER  length  \
name                                                                            
0:19412RT-Gen005-PCRfree-30X:cue            40148469     DEL     PASS    7856   
1:19412RT-Gen005-PCRfree-30X:cue            79648707     DEL     PASS    8758   
2:19412RT-Gen005-PCRfree-30X:cue            35145840     DEL     PASS    9593   
3:19412RT-Gen005-PCRfree-30X:cue            18547319     DEL     PASS    8266   
4:19412RT-Gen005-PCRfree-30X:cue           105916674     DEL     PASS    9791   
...                                              ...     ...      ...     ...   
53167:19412AL-Gen005-PCRfree-30X:delly_sv     173814     INV  LowQual       1   
53168:19412AL-Gen005-PCRfree-30X:delly_sv     742299     INV  LowQual       1   
53169:19412AL-Gen005-PCRfree-30X:delly_sv    2029974     INV  LowQual       1   
53170:19412AL-Gen005-PCRfree-30X:delly_sv    1984889     INV     PASS       1   
53171:19412AL-Gen005-PCRfree-30X:delly_sv    1984890     INV     PASS       1   

                                          interval_index    caller  \
name                                                                 
0:19412RT-Gen005-PCRfree-30X:cue                  210957       cue   
1:19412RT-Gen005-PCRfree-30X:cue                  212524       cue   
2:19412RT-Gen005-PCRfree-30X:cue                  210795       cue   
3:19412RT-Gen005-PCRfree-30X:cue                  210102       cue   
4:19412RT-Gen005-PCRfree-30X:cue                  213783       cue   
...                                                  ...       ...   
53167:19412AL-Gen005-PCRfree-30X:delly_sv         160290  delly_sv   
53168:19412AL-Gen005-PCRfree-30X:delly_sv          90067  delly_sv   
53169:19412AL-Gen005-PCRfree-30X:delly_sv          90069  delly_sv   
53170:19412AL-Gen005-PCRfree-30X:delly_sv          90068  delly_sv   
53171:19412AL-Gen005-PCRfree-30X:delly_sv          90068  delly_sv   

                                                               sample  \
name                                                                    
0:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X   
1:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X   
2:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X   
3:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X   
4:19412RT-Gen005-PCRfree-30X:cue           19412RT-Gen005-PCRfree-30X   
...                                                               ...   
53167:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X   
53168:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X   
53169:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X   
53170:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X   
53171:19412AL-Gen005-PCRfree-30X:delly_sv  19412AL-Gen005-PCRfree-30X   

                                          sample_short  FILTERbool  
name                                                        

In [193]:
SVs_bed_combined_annotated_Ana["FILTERbool"].value_counts()

False    456376
True     150129
Name: FILTERbool, dtype: int64

In [276]:
pv = pd.pivot_table(SVs_bed_combined_annotated_Ana,
               # values=SVs_bed_combined_annotated_Ana_wodups.columns,
               index=["interval_index"],
               columns=["caller","sample_short"],
               values=["FILTERbool"],
               aggfunc=sum
              )
pv

FILTERbool                                                    \
caller                cue                                                     
sample_short      19412AL 19412E 19412JR 19412RT 20487 20487A 20487J 20487N   
interval_index                                                                
0                     NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
1                     NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
2                     NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
3                     NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
4                     NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
...                   ...    ...     ...     ...   ...    ...    ...    ...   
292923                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
292924                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
292925                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
292926                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
292927                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   

                                                                           
caller         delly_sv                                                    
sample_short    19412AL 19412E 19412JR 19412RT 20487 20487A 20487J 20487N  
interval_index                                                             
0                   NaN    1.0     NaN     NaN   NaN    NaN    NaN    NaN  
1                   1.0    NaN     NaN     NaN   NaN    NaN    NaN    NaN  
2                   NaN    NaN     NaN     1.0   NaN    NaN    NaN    NaN  
3                   NaN    NaN     NaN     NaN   NaN    NaN    NaN    0.0  
4                   NaN    0.0     NaN     NaN   NaN    NaN    NaN    NaN  
...                 ...    ...     ...     ...   ...    ...    ...    ...  
292923              NaN    1.0     NaN     NaN   NaN    1.0    NaN    0.0  
292924              NaN    0.0     1.0     0.0   0.0    NaN    0.0    NaN  
292925              NaN    NaN     NaN     NaN   1.0    NaN    1.0    0.0  
292926              NaN    NaN     NaN     NaN   1.0    NaN    NaN    NaN  
292927              NaN    NaN     NaN     NaN   NaN    0.0    NaN    NaN  

[292928 rows x 16 columns]

In [203]:
not_found_in_controls = \
    (pd.isna(pv["FILTERbool","delly_sv"][controls_Ana]).sum(axis="columns")==len(controls_Ana)) * \
    (pd.isna(pv["FILTERbool","cue"][controls_Ana]).sum(axis="columns")==len(controls_Ana))

In [204]:
found_in_all_cases_by_any_method = \
    (pd.isna(pv["FILTERbool","delly_sv"][cases_Ana]).sum(axis=1)==0) + \
    (pd.isna(pv["FILTERbool","cue"][cases_Ana]).sum(axis=1)==0)

In [205]:
has_pass_flag_in_cases = \
    (pv["FILTERbool","delly_sv"][cases_Ana].fillna(value=0).sum(axis=1)>0) + \
    (pv["FILTERbool","cue"][cases_Ana].fillna(value=0).sum(axis=1)>0)

In [206]:
filt = not_found_in_controls & found_in_all_cases_by_any_method & has_pass_flag_in_cases

In [221]:
pv[filt]

FILTERbool                                                    \
caller                cue                                                     
sample_short      19412AL 19412E 19412JR 19412RT 20487 20487A 20487J 20487N   
interval_index                                                                
451                   NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
575                   NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
586                   NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
588                   NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
657                   NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
...                   ...    ...     ...     ...   ...    ...    ...    ...   
289273                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
290190                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
290931                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
290968                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   
292216                NaN    NaN     NaN     NaN   NaN    NaN    NaN    NaN   

                                                                           
caller         delly_sv                                                    
sample_short    19412AL 19412E 19412JR 19412RT 20487 20487A 20487J 20487N  
interval_index                                                             
451                 NaN    NaN     NaN     NaN   1.0    NaN    NaN    1.0  
575                 NaN    NaN     NaN     NaN   1.0    NaN    NaN    0.0  
586                 NaN    NaN     NaN     NaN   1.0    NaN    NaN    1.0  
588                 NaN    NaN     NaN     NaN   1.0    NaN    NaN    1.0  
657                 NaN    NaN     NaN     NaN   0.0    NaN    NaN    1.0  
...                 ...    ...     ...     ...   ...    ...    ...    ...  
289273              NaN    NaN     NaN     NaN   1.0    NaN    NaN    0.0  
290190              NaN    NaN     NaN     NaN   1.0    NaN    NaN    0.0  
290931              NaN    NaN     NaN     NaN   1.0    NaN    NaN    1.0  
290968              NaN    NaN     NaN     NaN   1.0    NaN    NaN    1.0  
292216              NaN    NaN     NaN     NaN   1.0    NaN    NaN    1.0  

[206 rows x 16 columns]

In [222]:
from IPython.display import display, HTML

pd.set_option('display.max_rows', 10)
display(SVs_bed_combined_annotated_Ana.set_index("interval_index").loc[pv[filt].index.values])
pd.set_option('display.max_rows', 10)
# with pd.option_context('display.max_rows', 100):
#     display(HTML(df))

/home/vfishman/miniconda3/envs/jupyter/lib/python3.8/site-packages/pandas/core/indexes/base.py:6982: FutureWarning: In a future version, the Index constructor will not infer numeric dtypes when passed object-dtype sequences (matching Series behavior)
  return Index(sequences[0], name=names)


chrm     start       end SV_type   FILTER  \
interval_index                                                              
451                     HLA-C*08:112      1052      1053     BND     PASS   
451                     HLA-C*08:112      1287      1288     BND     PASS   
575                HLA-DQA1*06:01:01      5365      5366     BND     PASS   
575                HLA-DQA1*06:01:01      4978      4979     BND  LowQual   
586             HLA-DQB1*03:01:01:01         4         5     BND     PASS   
...                              ...       ...       ...     ...      ...   
290931           chr6_KB021644v2_alt     49641     51388     DUP     PASS   
290968                          chr7    459593    459898     DUP     PASS   
290968                          chr7    459562    459860     DUP     PASS   
292216                          chrX  34420873  34424611     DUP     PASS   
292216                          chrX  34420913  34424578     DUP     PASS   

                length    caller                 sample sample_short  \
interval_index                                                         
451                  1  delly_sv   20487-Gen001-PCRfree        20487   
451                  1  delly_sv  20487N-Gen001-PCRfree       20487N   
575                  1  delly_sv   20487-Gen001-PCRfree        20487   
575                  1  delly_sv  20487N-Gen001-PCRfree       20487N   
586                  1  delly_sv   20487-Gen001-PCRfree        20487   
...                ...       ...                    ...          ...   
290931            1747  delly_sv  20487N-Gen001-PCRfree       20487N   
290968             305  delly_sv   20487-Gen001-PCRfree        20487   
290968             298  delly_sv  20487N-Gen001-PCRfree       20487N   
292216            3738  delly_sv   20487-Gen001-PCRfree        20487   
292216            3665  delly_sv  20487N-Gen001-PCRfree       20487N   

                FILTERbool  
interval_index              
451                   True  
451                   True  
575                   True  
575                  False  
586                   True  
...                    ...  
290931                True  
290968                True  
290968                True  
292216                True  
292216                True  

[496 rows x 10 columns]

In [227]:
filtered_Ana_HQ_or = SVs_bed_combined_annotated_Ana\
                        .drop_duplicates(subset="interval_index")\
                        .set_index("interval_index")\
                        .loc[pv[filt].index.values]\
                        .reset_index()
filtered_Ana_HQ_or

/home/vfishman/miniconda3/envs/jupyter/lib/python3.8/site-packages/pandas/core/indexes/base.py:6982: FutureWarning: In a future version, the Index constructor will not infer numeric dtypes when passed object-dtype sequences (matching Series behavior)
  return Index(sequences[0], name=names)


interval_index                  chrm     start       end SV_type  \
0               451          HLA-C*08:112      1052      1053     BND   
1               575     HLA-DQA1*06:01:01      5365      5366     BND   
2               586  HLA-DQB1*03:01:01:01         4         5     BND   
3               588  HLA-DQB1*03:01:01:01      1475      1476     BND   
4               657     HLA-DRB1*13:01:01      7476      7477     BND   
..              ...                   ...       ...       ...     ...   
201          289273                 chr20  61945504  61946376     DUP   
202          290190                  chr4  91379362  91403961     DUP   
203          290931   chr6_KB021644v2_alt     49747     51927     DUP   
204          290968                  chr7    459593    459898     DUP   
205          292216                  chrX  34420873  34424611     DUP   

      FILTER  length    caller                sample sample_short  FILTERbool  
0       PASS       1  delly_sv  20487-Gen001-PCRfree        20487        True  
1       PASS       1  delly_sv  20487-Gen001-PCRfree        20487        True  
2       PASS       1  delly_sv  20487-Gen001-PCRfree        20487        True  
3       PASS       1  delly_sv  20487-Gen001-PCRfree        20487        True  
4    LowQual       1  delly_sv  20487-Gen001-PCRfree        20487       False  
..       ...     ...       ...                   ...          ...         ...  
201     PASS     872  delly_sv  20487-Gen001-PCRfree        20487        True  
202     PASS   24599  delly_sv  20487-Gen001-PCRfree        20487        True  
203     PASS    2180  delly_sv  20487-Gen001-PCRfree        20487        True  
204     PASS     305  delly_sv  20487-Gen001-PCRfree        20487        True  
205     PASS    3738  delly_sv  20487-Gen001-PCRfree        20487        True  

[206 rows x 11 columns]

In [247]:
SVs_bed_combined_annotated.query("interval_index==283498")

chrm      start        end SV_type  \
name                                                                       
7383:20487-Gen001-PCRfree:delly_sv    chr6  115306250  125636522     DEL   
13864:20487N-Gen001-PCRfree:delly_sv  chr6  115306098  125636524     DEL   

                                       FILTER    length interval_index  \
name                                                                     
7383:20487-Gen001-PCRfree:delly_sv    LowQual  10330272         283498   
13864:20487N-Gen001-PCRfree:delly_sv     PASS  10330426         283498   

                                        caller                 sample  
name                                                                   
7383:20487-Gen001-PCRfree:delly_sv    delly_sv   20487-Gen001-PCRfree  
13864:20487N-Gen001-PCRfree:delly_sv  delly_sv  20487N-Gen001-PCRfree

In [235]:
OMIM_genes = pd.read_csv("mart_export_OMIM_genes.txt", sep="\t")
OMIM_genes["chrm"] = OMIM_genes["Chromosome/scaffold name"].apply(lambda x: "chr" + x)
OMIM_genes

Gene stable ID Chromosome/scaffold name  Gene start (bp)  \
0      ENSG00000000003                        X        100627108   
1      ENSG00000000005                        X        100584936   
2      ENSG00000000419                       20         50934867   
3      ENSG00000000457                        1        169849631   
4      ENSG00000000938                        1         27612064   
...                ...                      ...              ...   
14749  ENSG00000284536                       13         91350605   
14750  ENSG00000284547                        9        127785918   
14751  ENSG00000284565                       17         28861369   
14752  ENSG00000284567                        X         66018870   
14753  ENSG00000284690                       17         74560701   

       Gene end (bp) Gene name   chrm  
0          100639991    TSPAN6   chrX  
1          100599885      TNMD   chrX  
2           50959140      DPM1  chr20  
3          169894267     SCYL3   chr1  
4           27635185       FGR   chr1  
...              ...       ...    ...  
14749       91350688     MIR17  chr13  
14750      127786007   MIR2861   chr9  
14751       28861440   MIR451A  chr17  
14752       66018979    MIR223   chrX  
14753       74567343    CD300H  chr17  

[14754 rows x 6 columns]

In [270]:
NDD_genes = pd.read_csv("mart_export_NDD_genes.txt", sep="\t")
NDD_genes["chrm"] = NDD_genes["Chromosome/scaffold name"].apply(lambda x: "chr" + x)
NDD_genes_bt = pybedtools.BedTool.from_dataframe(
        NDD_genes[["chrm","Gene start (bp)","Gene end (bp)","Gene name"]]).sort()
filtered_SV_ANA_bt = pybedtools.BedTool.from_dataframe(
        filtered_Ana_HQ_or.drop_duplicates(subset=["interval_index"])[
                ["chrm","start","end","interval_index","SV_type","length","caller"]
    ]).sort()
filtered_SV_with_closest_genes_Ana = filtered_SV_ANA_bt.closest(NDD_genes_bt,d=True)

/home/vfishman/miniconda3/envs/jupyter/lib/python3.8/subprocess.py:849: RuntimeWarning: line buffering (buffering=1) isn't supported in binary mode, the default buffer size will be used
  self.stderr = io.open(errread, 'rb', bufsize)
/home/vfishman/miniconda3/envs/jupyter/lib/python3.8/subprocess.py:849: RuntimeWarning: line buffering (buffering=1) isn't supported in binary mode, the default buffer size will be used
  self.stderr = io.open(errread, 'rb', bufsize)
/home/vfishman/miniconda3/envs/jupyter/lib/python3.8/subprocess.py:849: RuntimeWarning: line buffering (buffering=1) isn't supported in binary mode, the default buffer size will be used
  self.stderr = io.open(errread, 'rb', bufsize)
***** WARNING: File /tmp/pybedtools.lds1j8n6.tmp has inconsistent naming convention for record:
chr1	944203	959309	NOC2L

***** WARNING: File /tmp/pybedtools.lds1j8n6.tmp has inconsistent naming convention for record:
chr1	944203	959309	NOC2L



In [271]:
pd.set_option('display.max_rows', 80)

filtered_SV_with_closest_genes_Ana.to_dataframe().\
                                rename(columns={
                                    "name":"interval_index",
                                    "score":"SV_type",
                                    "strand":"SV_len",
                                    "thickStart":"caller",
                                    "thickEnd":"geneChr",
                                    "itemRgb":"geneStart",
                                    "blockCount":"geneEnd",
                                    "blockSizes":"geneName",
                                    "blockStarts":"SV_distance"
                                }).\
                                query("SV_distance>=0").\
                                sort_values(by=["SV_distance"])[:80]
#                                query("blockStarts>0 and chrom=='chr6'").

chrom      start        end  interval_index SV_type    SV_len    caller  \
114  chr21   45089161   45089162          115109     INV         1  delly_sv   
39   chr12  129757949  129759267          206834     DEL      1318  delly_sv   
115  chr22   20929152   20930744          257494     DEL      1592  delly_sv   
176   chr6  115306250  125636522          283498     DEL  10330272  delly_sv   
168   chr6  115306250  125636522          283498     DEL  10330272  delly_sv   
169   chr6  115306250  125636522          283498     DEL  10330272  delly_sv   
55   chr15   28301274   28301275           83456     INV         1  delly_sv   
35   chr12   99764626   99764627           74854     INV         1  delly_sv   
170   chr6  115306250  125636522          283498     DEL  10330272  delly_sv   
172   chr6  115306250  125636522          283498     DEL  10330272  delly_sv   
173   chr6  115306250  125636522          283498     DEL  10330272  delly_sv   
73   chr17   11507921   11509113          225441     DEL      1192  delly_sv   
177   chr6  115306250  125636522          283498     DEL  10330272  delly_sv   
82   chr18   13883601   13883636          231997     DEL        35  delly_sv   
174   chr6  115306250  125636522          283498     DEL  10330272  delly_sv   
171   chr6  115306250  125636522          283498     DEL  10330272  delly_sv   
194   chr8   22396301   22397525          172290     DEL      1224  delly_sv   
175   chr6  115306250  125636522          283498     DEL  10330272  delly_sv   
200   chr9   36422131   36423984          178823     DEL      1853  delly_sv   
145   chr4  150966423  150968284          271793     DEL      1861  delly_sv   
201   chr9   70193541   70193542          157485     INV         1  delly_sv   
6     chr1    7270208    7270243          224781     DEL        35  delly_sv   
211   chrX   78072378   78072709          186827     DEL       331  delly_sv   
206   chr9  130456334  130457647          182071     DEL      1313  delly_sv   
111  chr20   63655732   63657292          254866     DEL      1560  delly_sv   
89   chr19   12876189   12877529          236005     DEL      1340  delly_sv   
110  chr20   61945504   61946376          289273     DUP       872  delly_sv   
207   chr9  133366717  133367482          182314     DEL       765  delly_sv   
85   chr19    3711066    3711067           19141     BND         1  delly_sv   
17   chr10   32068319   32069377          178929     DEL      1058  delly_sv   
59   chr15   90984153   90985714          217641     DEL      1561  delly_sv   
120   chr3   24670868   24670895          261230     DEL        27  delly_sv   
193   chr7  155482135  155482635          171183     DEL       500  delly_sv   
101   chr2  142856559  142858420          247519     DEL      1861  delly_sv   
125   chr3  113726916  113726917          121223     INV         1  delly_sv   
124   chr3  113726056  113726057          121222     INV         1  delly_sv   
96   chr19   39456957   39456958           98968     INV         1  delly_sv   
147   chr5     282884     284647          272998     DEL      1763  delly_sv   
46   chr14   34954588   34956074          210761     DEL      1486  delly_sv   
9     chr1   22991693   22992804          193969     DEL      1111  delly_sv   
191   chr7  102311907  102313678          169269     DEL      1771  delly_sv   
7     chr1   10824654   10824685          265448     DEL        31  delly_sv   
29   chr11  116818070  116818097          198843     DEL        27  delly_sv   
77   chr17   75719006   75720449          230259     DEL      1443  delly_sv   
131   chr3  196866748  196866749          124339     INV         1  delly_sv   
70   chr16   69374627   69374664          223031     DEL        37  delly_sv   
26   chr11   66809590   66811311          197049     DEL      1721  delly_sv   
78   chr17   75823152   75823153           93660     INV         1  delly_sv   
133   chr4     744705     747677          267475     DEL      2972  delly_sv   
167  

In [ ]:
# chr15 28301274 28610633	 ---> Poor region, to few supporting reads, HERC 2 has AR pattern

# chr18	13883601	13883636	231997	DEL	35 ---> interesting, deletion in 3'-UTR of MC2R gene, 
# confirmed in bam-file, present only in probands (not in parents). But MC2R pehenotype is AR & it's UTR...



<h1> Ana X-linked </h1>

In [280]:
controls_and_father_Ana = ["19412AL", "19412E", "19412JR", "19412RT","20487A"]
cases_and_mother_Ana = ["20487","20487N","20487J"]
not_found_in_controls_and_father = \
    (pd.isna(pv["FILTERbool","delly_sv"][controls_and_father_Ana]).sum(axis="columns")==len(controls_and_father_Ana)) * \
    (pd.isna(pv["FILTERbool","cue"][controls_and_father_Ana]).sum(axis="columns")==len(controls_and_father_Ana))
print (sum(not_found_in_controls_and_father))
found_in_all_cases_and_mother_by_any_method = \
    (pd.isna(pv["FILTERbool","delly_sv"][cases_and_mother_Ana]).sum(axis=1)==0) + \
    (pd.isna(pv["FILTERbool","cue"][cases_and_mother_Ana]).sum(axis=1)==0)
has_pass_flag_in_cases = \
    (pv["FILTERbool","delly_sv"][cases_and_mother_Ana].fillna(value=0).sum(axis=1)>0) + \
    (pv["FILTERbool","cue"][cases_and_mother_Ana].fillna(value=0).sum(axis=1)>0)

X_filt = not_found_in_controls_and_father & found_in_all_cases_and_mother_by_any_method & has_pass_flag_in_cases
print(sum(X_filt))
filtered_Ana_Xlinked = SVs_bed_combined_annotated_Ana\
                        .drop_duplicates(subset="interval_index")\
                        .set_index("interval_index")\
                        .loc[pv[X_filt].index.values]\
                        .reset_index()
filtered_Ana_Xlinked
filtered_Ana_Xlinked_bt = pybedtools.BedTool.from_dataframe(
        filtered_Ana_Xlinked.drop_duplicates(subset=["interval_index"])[
                ["chrm","start","end","interval_index","SV_type","length","caller"]
    ]).sort()
filtered_Ana_Xlinked_with_closest_genes_Ana = filtered_Ana_Xlinked_bt.closest(NDD_genes_bt,d=True)
filtered_Ana_Xlinked_with_closest_genes_Ana.to_dataframe().\
                                rename(columns={
                                    "name":"interval_index",
                                    "score":"SV_type",
                                    "strand":"SV_len",
                                    "thickStart":"caller",
                                    "thickEnd":"geneChr",
                                    "itemRgb":"geneStart",
                                    "blockCount":"geneEnd",
                                    "blockSizes":"geneName",
                                    "blockStarts":"SV_distance"
                                }).\
                                query("chrom=='chrX'").\
                                query("SV_distance>=0").\
                                sort_values(by=["SV_distance"])[:80]

101423
556


/home/vfishman/miniconda3/envs/jupyter/lib/python3.8/site-packages/pandas/core/indexes/base.py:6982: FutureWarning: In a future version, the Index constructor will not infer numeric dtypes when passed object-dtype sequences (matching Series behavior)
  return Index(sequences[0], name=names)
/home/vfishman/miniconda3/envs/jupyter/lib/python3.8/subprocess.py:849: RuntimeWarning: line buffering (buffering=1) isn't supported in binary mode, the default buffer size will be used
  self.stderr = io.open(errread, 'rb', bufsize)
/home/vfishman/miniconda3/envs/jupyter/lib/python3.8/subprocess.py:849: RuntimeWarning: line buffering (buffering=1) isn't supported in binary mode, the default buffer size will be used
  self.stderr = io.open(errread, 'rb', bufsize)
***** WARNING: File /tmp/pybedtools.lds1j8n6.tmp has inconsistent naming convention for record:
chr1	944203	959309	NOC2L

***** WARNING: File /tmp/pybedtools.lds1j8n6.tmp has inconsistent naming convention for record:
chr1	944203	959309	NOC

chrom      start        end  interval_index SV_type   SV_len    caller  \
555  chrX   41829696   41829741          185352     DEL       45  delly_sv   
546  chrX   37651918   42011746          185210     DEL  4359828  delly_sv   
547  chrX   37651918   42011746          185210     DEL  4359828  delly_sv   
548  chrX   37651918   42011746          185210     DEL  4359828  delly_sv   
549  chrX   37651918   42011746          185210     DEL  4359828  delly_sv   
550  chrX   37651918   42011746          185210     DEL  4359828  delly_sv   
551  chrX   37651918   42011746          185210     DEL  4359828  delly_sv   
552  chrX   37651918   42011746          185210     DEL  4359828  delly_sv   
553  chrX   37651918   42011746          185210     DEL  4359828  delly_sv   
554  chrX   38893030   40251873          292221     DUP  1358843  delly_sv   
585  chrX  155688459  155688460          163778     INV        1  delly_sv   
557  chrX   43809946   43810269          185375     DEL      323  delly_sv   
561  chrX   45048880   45048881           45850     BND        1  delly_sv   
562  chrX   47911384   47911468          185537     DEL       84  delly_sv   
564  chrX   49966593   49968963          185658     DEL     2370  delly_sv   
571  chrX   72248291   72248319          186723     DEL       28  delly_sv   
545  chrX   37651918   42011746          185210     DEL  4359828  delly_sv   
544  chrX   37651918   42011746          185210     DEL  4359828  delly_sv   
586  chrX  155688459  155688460          163778     INV        1  delly_sv   
542  chrX   37651837   42010600          292220     DUP  4358763  delly_sv   
543  chrX   37651918   42011746          185210     DEL  4359828  delly_sv   
527  chrX   32738668   32738669          161175     INV        1  delly_sv   
528  chrX   32901410   32903318          185164     DEL     1908  delly_sv   
526  chrX   32227264   32227293          185153     DEL       29  delly_sv   
532  chrX   37651837   42010600          292220     DUP  4358763  delly_sv   
533  chrX   37651837   42010600          292220     DUP  4358763  delly_sv   
534  chrX   37651837   42010600          292220     DUP  4358763  delly_sv   
531  chrX   36364901   36364932          185197     DEL       31  delly_sv   
536  chrX   37651837   42010600          292220     DUP  4358763  delly_sv   
537  chrX   37651837   42010600          292220     DUP  4358763  delly_sv   
538  chrX   37651837   42010600          292220     DUP  4358763  delly_sv   
539  chrX   37651837   42010600          292220     DUP  4358763  delly_sv   
540  chrX   37651837   42010600          292220     DUP  4358763  delly_sv   
541  chrX   37651837   42010600          292220     DUP  4358763  delly_sv   
535  chrX   37651837   42010600          292220     DUP  4358763  delly_sv   
568  chrX   65538494   65538529          186524     DEL       35  delly_sv   
558  chrX   43995491   44085583          292224     DUP    90092  delly_sv   
559  chrX   43995619   44088121          185376     DEL    92502  delly_sv   
563  chrX   48642116   48644542          185591     DEL     2426  delly_sv   
560  chrX   44085586   44088085          185377     DEL     2499  delly_sv   
572  chrX   78260497   78268592          186832     DEL     8095  delly_sv   
576  chrX   85077475   85077476          162319     INV        1       cue   
570  chrX   70947956   70947983          186654     DEL       27  delly_sv   
525  chrX   22826248   22826249           45448     BND        1  delly_sv   
530  chrX   35695983   35697882          185192     DEL     1899  delly_sv   
577  chrX   85546598   85546631          186909     DEL       33  delly_sv   
529  chrX   34604879   34604880           45674     BND        1  delly_sv   
567  chrX   63264707   63264708          161770     INV        1  delly_sv   
578  chrX   86470037   86470111          186916     DEL       74  delly_sv   
575  chrX   84807914   84807915          162308     INV        1       cue   
579  chrX   87024051   870

In [ ]:
# chrX	45048880	45048881 KDM6A
# chrX	47911384	47911468 ZNF81 --> lverlaps common SVs

chrX	65538494	65538529

<h1>Drafts2</h1>

In [6]:
class genomic_inerval():
    def __init__(self, chrom, st, end):
        self.chrom = chrom
        self.st = st
        self.end = end
        assert self.st <= self.end
    def __eq__(self, other):
        if not self.chrom == other.chrom:
            return result
        if other.end >= self.st >= other.st or other.end >= self.end >= other.st:
            return True
        else:
            return False
    def __repr__(self):
        return " ".join(map(str,[self.chrom, self.st, self.end]))

    def __str__(self):
        return self.__repr__()

In [7]:
pos1 = genomic_inerval("1", 10, 20)
pos2 = genomic_inerval("1", 30, 40)
pos3 = genomic_inerval("1", 5, 15)
pos4 = genomic_inerval("1", 50, 60)

pos4

1 50 60

In [9]:
a = pd.DataFrame({"pos":[pos1,pos2],"names":["a1","a2"]})
a

pos names
0  1 10 20    a1
1  1 30 40    a2

In [11]:
b = pd.DataFrame({"pos":[pos3,pos4],"names":["b1","b2"]})
b

pos names
0   1 5 15    b1
1  1 50 60    b2

In [13]:
pd.merge(a,b,on="pos")

TypeError: unhashable type: 'genomic_inerval'

In [16]:
from sympy import Interval, Union

In [17]:
df = pd.DataFrame({'chrom': ['chr1','chr1','chr1','chr1','chr1'], 
    'start': [1, 2, 5, 15, 30],
    'end': [10, 3, 20, 25, 40],
    'probability': [0.99, 0.99, 0.99, 0.99, 0.75],
    'read': ['read1','read2','read2','read2','read4']})
df

chrom  start  end  probability   read
0  chr1      1   10         0.99  read1
1  chr1      2    3         0.99  read2
2  chr1      5   20         0.99  read2
3  chr1     15   25         0.99  read2
4  chr1     30   40         0.75  read4

In [21]:
# Union intervals by @CentAu
from sympy import Interval, Union
def union(data):
    """ Union of a list of intervals e.g. [(1,2),(3,4)] """
    intervals = [Interval(begin, end) for (begin, end) in data]
    u = Union(*intervals)
    return [u] if isinstance(u, Interval) \
       else list(u.args)

# Get intervals for rows
def f(x,position=None):
    """
    Returns an interval for the row. The start and stop position indicate the minimum
        and maximum position of all overlapping ranges within the group.
    Args: 
        position (str, optional): Returns an integer indicating start or stop position.
    """
    intervals = union(x)
    print (x)
    print (intervals)
    raise
    if position and position.lower() == 'start':
        group = x.str[0].apply(lambda y: [l.start for g,l in enumerate(intervals) if l.contains(y)][0])
    elif position and position.lower() == 'end':
        group = x.str[0].apply(lambda y: [l.end for g,l in enumerate(intervals) if l.contains(y)][0])
    else:
        group = x.str[0].apply(lambda y: [l for g,l in enumerate(intervals) if l.contains(y)][0])
    return group




In [22]:
# Combine start and end into a single column
df['start_end'] = df[['start', 'end']].apply(list, axis=1)
df

chrom  start  end  probability   read start_end start_interval
0  chr1      1   10         0.99  read1   [1, 10]              1
1  chr1      2    3         0.99  read2    [2, 3]              1
2  chr1      5   20         0.99  read2   [5, 20]              1
3  chr1     15   25         0.99  read2  [15, 25]              1
4  chr1     30   40         0.75  read4  [30, 40]             30

In [23]:

# Assign each row to an interval and add start/end columns
df['start_interval'] = df[['chrom',
    'start_end']].groupby(['chrom']).transform(f,'start')
df

0     [1, 10]
1      [2, 3]
2     [5, 20]
3    [15, 25]
4    [30, 40]
Name: start_end, dtype: object
[Interval(1, 25), Interval(30, 40)]


RuntimeError: No active exception to reraise

In [ ]:
df['end_interval'] = df[['chrom',
    'start_end']].groupby(['chrom']).transform(f,'end')

# Aggregate rows, using approach by @W-B
df.groupby(['chrom','start_interval','end_interval']).agg({'probability':'sum',
'read':'nunique'}).reset_index()

<h1>Drafts</h1>

In [219]:
d = pd.DataFrame.from_records(
    [("1",100,200,"a","DEL"),
     ("1",110,210,"b","DEL"),
     ("1",111,211,"c","DEL"),
     ("1",190,290,"d","DEL"),
     ("1",195,290,"e","DEL"),
     ("2",100,200,"f","DEL")], columns = ["chrm","start","end","name","SV_type"])
d

chrm  start  end name SV_type
0    1    100  200    a     DEL
1    1    110  210    b     DEL
2    1    111  211    c     DEL
3    1    190  290    d     DEL
4    1    195  290    e     DEL
5    2    100  200    f     DEL

In [290]:
colnames = ["chrm","start","end","name","SV_type"]
btool = pybedtools.BedTool.from_dataframe(
        d[colnames])
sorted  = btool.sort()
min_merge_overlap = 0.6
intersect = sorted.intersect(sorted, 
                                 f=min_merge_overlap,
                                 r=True,sorted=True,
                                 wa=True,
                                 wb=True)
                                 # .to_dataframe()


/home/vfishman/miniconda3/envs/jupyter/lib/python3.8/subprocess.py:849: RuntimeWarning: line buffering (buffering=1) isn't supported in binary mode, the default buffer size will be used
  self.stderr = io.open(errread, 'rb', bufsize)
/home/vfishman/miniconda3/envs/jupyter/lib/python3.8/subprocess.py:849: RuntimeWarning: line buffering (buffering=1) isn't supported in binary mode, the default buffer size will be used
  self.stderr = io.open(errread, 'rb', bufsize)


In [291]:
intersect = intersect.to_dataframe()
intersect

chrom  start  end name score  strand  thickStart  thickEnd itemRgb  \
0       1    100  200    a   DEL       1         100       200       a   
1       1    100  200    a   DEL       1         110       210       b   
2       1    100  200    a   DEL       1         111       211       c   
3       1    110  210    b   DEL       1         100       200       a   
4       1    110  210    b   DEL       1         110       210       b   
5       1    110  210    b   DEL       1         111       211       c   
6       1    111  211    c   DEL       1         100       200       a   
7       1    111  211    c   DEL       1         110       210       b   
8       1    111  211    c   DEL       1         111       211       c   
9       1    190  290    d   DEL       1         190       290       d   
10      1    190  290    d   DEL       1         195       290       e   
11      1    195  290    e   DEL       1         190       290       d   
12      1    195  290    e   DEL       1         195       290       e   
13      2    100  200    f   DEL       2         100       200       f   

   blockCount  
0         DEL  
1         DEL  
2         DEL  
3         DEL  
4         DEL  
5         DEL  
6         DEL  
7         DEL  
8         DEL  
9         DEL  
10        DEL  
11        DEL  
12        DEL  
13        DEL

In [338]:
clusters = networkx.connected_components(g)
sorted_as_df = sorted.to_dataframe()
sorted_as_df.columns = colnames
sorted_as_df["interval_index"] = pd.NA
assert not np.any(sorted_as_df["name"].duplicated())
sorted_as_df = sorted_as_df.set_index("name")
for cluster_id,cluster in tqdm(enumerate(clusters)):
    sorted_as_df.loc[cluster,"interval_index"] = str(cluster_id)
sorted_as_df.loc[:,"interval_index"] = sorted_as_df.apply(
                                            lambda x: x["interval_index"]+":"+x["SV_type"],
                                            axis="columns"
                                        ) 
sorted_as_df
sorted_as_df.reset_index(drop=False).groupby("interval_index").agg({
    "name": lambda x: ",".join(x),
    "start": min,
    "end": max,
    "SV_type":lambda x: list(x)[0],
    "chrm":lambda x: list(x)[0]
}
).reset_index(drop=False).rename(columns={"chrm":"chrom"})


0it [00:00, ?it/s]

/tmp/ipykernel_6433/2736564386.py:8: FutureWarning: Passing a set as an indexer is deprecated and will raise in a future version. Use a list instead.
  sorted_as_df.loc[cluster,"interval_index"] = str(cluster_id)
/tmp/ipykernel_6433/2736564386.py:8: FutureWarning: Passing a set as an indexer is deprecated and will raise in a future version. Use a list instead.
  sorted_as_df.loc[cluster,"interval_index"] = str(cluster_id)
/tmp/ipykernel_6433/2736564386.py:8: FutureWarning: Passing a set as an indexer is deprecated and will raise in a future version. Use a list instead.
  sorted_as_df.loc[cluster,"interval_index"] = str(cluster_id)


interval_index   name  start  end SV_type  chrom
0          0:DEL  a,b,c    100  211     DEL      1
1          1:DEL    d,e    190  290     DEL      1
2          2:DEL      f    100  200     DEL      2

{'a', 'b', 'c'}